##### Import Packages

In [1]:
# Import the required libraries and packages

import pandas as pd
import numpy as np
import math
import itertools
import warnings
warnings.filterwarnings('ignore')
import datetime as dt
from datetime import datetime
from scipy import stats
from scipy.stats import norm
import statsmodels.api as sm

pd.options.display.max_rows = 1200
pd.options.display.max_columns = 1000

###### Read data into notebook

In [2]:
# read csv into notebook
# Ensure to replace the file path location

col_names = ['Oil Prices', 'Inflation', 'NSE ASI', 'FX Reserves', 'USD/NGN (BDC)', 
             'USD/NGN (I&E)', '91-Day Yield', '182-Day Yield', '364-Day Yield', 
             '2yr-Bond Yield', '3yr-Bond Yield', '5yr-Bond Yield', '7yr-Bond Yield', 
             '10yr-Bond Yield', '12yr-Bond Yield', '15yr-Bond Yield', '20yr-Bond Yield']


axa_mmf_ = pd.read_csv(r'C:\Users\HP\Python University\Wealth Hat\axa_mmf1.csv')
fund_prices = pd.read_csv(r'C:\Users\HP\Python University\Wealth Hat\fund_prices (version 1).csv')
macro_data = pd.read_csv(r'C:\Users\HP\Python University\Wealth Hat\Portfolios & Macro Data.csv', usecols = col_names)

In [3]:
# Reset date format

fund_prices['Date'] = pd.to_datetime(fund_prices.Date, format = '%Y-%m-%d') 
axa_mmf_['Date'] = pd.to_datetime(axa_mmf_.Date, format = '%Y-%m-%d')

In [4]:
# Calculate the daily yields
axa_mmf_['AXA Money Market Fund Yield'] = (1 + axa_mmf_['AXA Money Market Fund Yield']) ** (1/365) - 1

In [5]:
# Summarize the datetime format to (Year-Month)

axa_mmf_['year month'] = axa_mmf_['Date'].apply(lambda x: x.strftime('%Y-%m'))
axa_mmf_ = axa_mmf_.drop(columns = ['Date'], axis = 1)

In [6]:
# Calculate the monthly returns from daily yields
axa_mmf_ = axa_mmf_.groupby('year month')['AXA Money Market Fund Yield'].sum().reset_index()

### Monthly Returns

In [7]:
# Create a copy of the dataset

fund_prices = fund_prices.copy()

In [8]:
# extract some date information

fund_prices['year'] = fund_prices['Date'].dt.year
fund_prices['month'] = fund_prices['Date'].dt.month
fund_prices['day'] = fund_prices['Date'].dt.day
fund_prices['day of month'] = fund_prices['Date'].dt.daysinmonth

In [9]:
# Extract the first and last days of each month

first_day28 = fund_prices[(fund_prices['day'] == 1) & (fund_prices['day of month'] == 28)]
last_day28 = fund_prices[(fund_prices['day'] == 28) & (fund_prices['day of month'] == 28)]
first_day30 = fund_prices[(fund_prices['day'] == 1) & (fund_prices['day of month'] == 30)]
last_day30 = fund_prices[(fund_prices['day'] == 30) & (fund_prices['day of month'] == 30)]
first_day31 = fund_prices[(fund_prices['day'] == 1) & (fund_prices['day of month'] == 31)]
last_day31 = fund_prices[(fund_prices['day'] == 31) & (fund_prices['day of month'] == 31)]

In [10]:
# Concatenate the first and last days rows to form new dataset

new_prices = pd.concat([first_day28, last_day28, first_day30, last_day30, first_day31, last_day31], axis = 0)

In [11]:
# Summarise the datetime format to (Year-Month) and rearrange the index

new_prices['year month'] = new_prices['Date'].apply(lambda x: x.strftime('%Y-%m'))
new_prices = new_prices.sort_index(ascending = True)

In [12]:
# Summarise the datetime format to (Year-Month) and rearrange the index

new_prices['year month'] = new_prices['Date'].apply(lambda x: x.strftime('%Y-%m'))
new_prices = new_prices.sort_index(ascending = True)

In [13]:
new_prices1 = new_prices[['year month', 'Stanbic ETF 30', 'Stanbic Absolute Fund', 
            'Stanbic Guaranteed Income Fund', 'Stanbic Eurobond Fund', 
            'FBN Eurobond Fund']].reset_index(drop = True)

In [14]:
stb_etf_returns = new_prices1['Stanbic ETF 30'].div(new_prices1.groupby('year month')['Stanbic ETF 30'].shift(1)) - 1
stb_abs_returns = new_prices1['Stanbic Absolute Fund'].div(new_prices1.groupby('year month')['Stanbic Absolute Fund'].shift(1)) - 1
stb_gtd_returns = new_prices1['Stanbic Guaranteed Income Fund'].div(new_prices1.groupby('year month')['Stanbic Guaranteed Income Fund'].shift(1)) - 1
stb_euro_returns = new_prices1['Stanbic Eurobond Fund'].div(new_prices1.groupby('year month')['Stanbic Eurobond Fund'].shift(1)) - 1
fbn_euro_returns = new_prices1['FBN Eurobond Fund'].div(new_prices1.groupby('year month')['FBN Eurobond Fund'].shift(1)) - 1

In [15]:
dates = pd.date_range(start = '08-01-2016', periods = 28, freq = 'M')
dates.to_period('M')

PeriodIndex(['2016-08', '2016-09', '2016-10', '2016-11', '2016-12', '2017-01',
             '2017-02', '2017-03', '2017-04', '2017-05', '2017-06', '2017-07',
             '2017-08', '2017-09', '2017-10', '2017-11', '2017-12', '2018-01',
             '2018-02', '2018-03', '2018-04', '2018-05', '2018-06', '2018-07',
             '2018-08', '2018-09', '2018-10', '2018-11'],
            dtype='period[M]', freq='M')

In [16]:
# Create new dataframe from the percentage change values

monthly_returns = pd.DataFrame()

#monthly_returns['Date'] = dates.to_period('M')
monthly_returns['Stanbic ETF 30'] = stb_etf_returns
monthly_returns['Stanbic Absolute Fund'] = stb_abs_returns
monthly_returns['Stanbic Guaranteed Income Fund'] = stb_gtd_returns
monthly_returns['Stanbic Eurobond Fund'] = stb_euro_returns
monthly_returns['FBN Eurobond Fund'] = fbn_euro_returns

In [17]:
# Concatenate the AXA MMF monthly yields values to the new monthly_returns dataframe

monthly_returns = monthly_returns.dropna()
monthly_returns = monthly_returns.reset_index(drop = True, inplace = False)
month_returns = pd.concat([monthly_returns, axa_mmf_], axis = 1)

###### Calculate Portfolio Returns

In [18]:
returns1 = month_returns[['Stanbic Absolute Fund', 'AXA Money Market Fund Yield']]
returns2 = month_returns[['Stanbic Absolute Fund', 'Stanbic Guaranteed Income Fund', 'AXA Money Market Fund Yield']]            
returns3 = month_returns[['Stanbic Absolute Fund', 'Stanbic ETF 30']]
returns4 = month_returns[['Stanbic Eurobond Fund', 'FBN Eurobond Fund']]

In [19]:
# Asset weighting in portfolio

axa_mmf1, axa_mmf2, axa_mmf3 = [0.9, 0.72, 0.13]
stb_abs1, stb_abs2, stb_abs3, stb_abs4, stb_abs5 = [0.1, 0.24, 0.87, 0.73, 0.51]
stb_GI = 0.04
stb_etf1, stb_etf2 = [0.27, 0.49]
stb_euro, fbn_euro = [0.5, 0.5]

In [20]:
conserv = np.array([stb_abs1, axa_mmf1])
caut = np.array([stb_abs2, stb_GI, axa_mmf2])
bal = np.array([stb_abs3, axa_mmf3])
grow = np.array([stb_abs4, stb_etf1])
aggres = np.array([stb_abs5, stb_etf2])
doll = np.array([stb_euro, fbn_euro])

In [21]:
conservative = np.dot(returns1, conserv)
cautious = np.dot(returns2, caut)
balanced = np.dot(returns1, bal)
growth = np.dot(returns3, grow)
aggressive = np.dot(returns3, aggres)
dollar = np.dot(returns4, doll)

In [22]:
# Create dataframe from calculated portfolio returns

portfolios = pd.DataFrame()

portfolios['Date'] = dates.to_period('M')
portfolios['Conservative'] = conservative
portfolios['Cautious'] = cautious
portfolios['Balanced'] = balanced
portfolios['Growth'] = growth
portfolios['Aggressive'] = aggressive
portfolios['Dollar'] = dollar

### Regression

In [23]:
data = pd.concat([portfolios, macro_data], axis = 1)

In [24]:
# Independent Variables

X1 = data[['Oil Prices', 'Inflation', 'NSE ASI', 'FX Reserves', 'USD/NGN (BDC)', 'USD/NGN (I&E)', '91-Day Yield', 
           '182-Day Yield', '364-Day Yield', '2yr-Bond Yield', '3yr-Bond Yield', '5yr-Bond Yield', '7yr-Bond Yield', 
           '10yr-Bond Yield', '12yr-Bond Yield', '15yr-Bond Yield', '20yr-Bond Yield']]

###### Conservative Portfolio

In [25]:
Y1 = data['Conservative']                              # Dependent variable
X1a = sm.add_constant(X1)
reg1 = sm.OLS(Y1, X1a).fit()
#prediction1 = reg1.predict(X1)

reg1.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:           Conservative   R-squared:                       0.734
Model:                            OLS   Adj. R-squared:                  0.281
Method:                 Least Squares   F-statistic:                     1.621
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.220
Time:                        05:49:04   Log-Likelihood:                 148.26
No. Observations:                  28   AIC:                            -260.5
Df Residuals:                      10   BIC:                            -236.5
Df Model:                          17                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const               0.0107      0.001     19.743      0.000       0.010       0.012
Oil Prices          0.0061      0.008      0.775      0.456      -0.011       0.024
Inflation          -0.0051      0.018     -0.285      0.782      -0.045       0.035
NSE ASI             0.0207      0.008      2.731      0.021       0.004       0.038
FX Reserves         0.0251      0.013      1.986      0.075      -0.003       0.053
USD/NGN (BDC)      -0.0189      0.011     -1.671      0.126      -0.044       0.006
USD/NGN (I&E)       0.0094      0.010      0.914      0.382      -0.013       0.032
91-Day Yield        0.0006      0.005      0.117      0.909      -0.011       0.013
182-Day Yield      -0.0033      0.009     -0.352      0.732      -0.024       0.018
364-Day Yield       0.0007      0.012      0.058      0.955      -0.026       0.027
2yr-Bond Yield     -0.0062      0.015     -0.410      0.690      -0.040       0.027
3yr-Bond Yield      0.0208      0.031      0.674      0.516      -0.048       0.089
5yr-Bond Yield      0.0049      0.048      0.102      0.920      -0.102       0.112
7yr-Bond Yield     -0.0199      0.072     -0.277      0.787      -0.180       0.140
10yr-Bond Yield    -0.0041      0.087     -0.047      0.963      -0.197       0.189
12yr-Bond Yield     0.0663      0.160      0.415      0.687      -0.290       0.422
15yr-Bond Yield    -0.0406      0.112     -0.362      0.725      -0.291       0.210
20yr-Bond Yield    -0.0209      0.058     -0.358      0.728      -0.151       0.109
==============================================================================
Omnibus:                        4.125   Durbin-Watson:                   1.533
Prob(Omnibus):                  0.127   Jarque-Bera (JB):                2.519
Skew:                           0.500   Prob(JB):                        0.284
Kurtosis:                       4.076   Cond. No.                         514.
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [26]:
# Independent Variables: These variables exhibited a relationship with the dependent variable 
# (Conservative Portfolio). Re-ran the regression with the variables.

X1_conserv = data[['NSE ASI', 'FX Reserves', 'USD/NGN (BDC)']]          # Independent variable
Y1_conserv = data['Conservative']                                       # Dependent variable
X1a_conserv = sm.add_constant(X1_conserv)
reg1_conserv = sm.OLS(Y1_conserv, X1a_conserv).fit()
#prediction1 = reg1.predict(X1)

reg1_conserv.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:           Conservative   R-squared:                       0.574
Model:                            OLS   Adj. R-squared:                  0.520
Method:                 Least Squares   F-statistic:                     10.76
Date:                Sun, 28 Jun 2020   Prob (F-statistic):           0.000114
Time:                        05:49:05   Log-Likelihood:                 141.66
No. Observations:                  28   AIC:                            -275.3
Df Residuals:                      24   BIC:                            -270.0
Df Model:                           3                                         
Covariance Type:            nonrobust                                         
=================================================================================
                    coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------
const             0.0111      0.000     31.890      0.000       0.010       0.012
NSE ASI           0.0187      0.005      3.687      0.001       0.008       0.029
FX Reserves       0.0244      0.007      3.332      0.003       0.009       0.040
USD/NGN (BDC)    -0.0143      0.005     -3.047      0.006      -0.024      -0.005
==============================================================================
Omnibus:                        0.067   Durbin-Watson:                   1.405
Prob(Omnibus):                  0.967   Jarque-Bera (JB):                0.287
Skew:                          -0.005   Prob(JB):                        0.867
Kurtosis:                       2.505   Cond. No.                         23.4
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

###### Cautious Portfolio

In [27]:
Y2 = data['Cautious']                               # Dependent variable
X1b = sm.add_constant(X1)
reg2 = sm.OLS(Y2, X1b).fit()
#prediction1 = reg1.predict(X1)

reg2.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               Cautious   R-squared:                       0.743
Model:                            OLS   Adj. R-squared:                  0.306
Method:                 Least Squares   F-statistic:                     1.701
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.197
Time:                        05:49:05   Log-Likelihood:                 148.24
No. Observations:                  28   AIC:                            -260.5
Df Residuals:                      10   BIC:                            -236.5
Df Model:                          17                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const               0.0109      0.001     20.009      0.000       0.010       0.012
Oil Prices          0.0049      0.008      0.621      0.549      -0.013       0.023
Inflation          -0.0026      0.018     -0.143      0.889      -0.042       0.037
NSE ASI             0.0211      0.008      2.787      0.019       0.004       0.038
FX Reserves         0.0257      0.013      2.036      0.069      -0.002       0.054
USD/NGN (BDC)      -0.0195      0.011     -1.724      0.115      -0.045       0.006
USD/NGN (I&E)       0.0098      0.010      0.954      0.363      -0.013       0.033
91-Day Yield        0.0013      0.005      0.237      0.817      -0.011       0.013
182-Day Yield      -0.0034      0.009     -0.360      0.726      -0.024       0.017
364-Day Yield      -0.0033      0.012     -0.277      0.788      -0.030       0.023
2yr-Bond Yield     -0.0077      0.015     -0.513      0.619      -0.041       0.026
3yr-Bond Yield      0.0283      0.031      0.918      0.380      -0.040       0.097
5yr-Bond Yield      0.0119      0.048      0.247      0.810      -0.095       0.119
7yr-Bond Yield     -0.0443      0.072     -0.617      0.551      -0.204       0.116
10yr-Bond Yield    -0.0093      0.087     -0.107      0.917      -0.203       0.184
12yr-Bond Yield     0.0452      0.160      0.283      0.783      -0.311       0.401
15yr-Bond Yield    -0.0144      0.112     -0.128      0.900      -0.265       0.236
20yr-Bond Yield    -0.0040      0.058     -0.068      0.947      -0.134       0.126
==============================================================================
Omnibus:                        4.636   Durbin-Watson:                   1.723
Prob(Omnibus):                  0.098   Jarque-Bera (JB):                2.945
Skew:                           0.579   Prob(JB):                        0.229
Kurtosis:                       4.087   Cond. No.                         514.
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [28]:
# Some independent variables exhibited a relationship with the dependent variable 
# (Cautious Portfolio). Re-ran the regression with the variables.

X1_caut = data[['NSE ASI', '12yr-Bond Yield']]        # Indepedent variable
Y2_caut = data['Balanced']                            # Dependent variable
X1b_caut = sm.add_constant(X1_caut)
reg2_caut = sm.OLS(Y2_caut, X1b_caut).fit()
#prediction1 = reg1.predict(X1)

reg2_caut.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               Balanced   R-squared:                       0.160
Model:                            OLS   Adj. R-squared:                  0.093
Method:                 Least Squares   F-statistic:                     2.389
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.112
Time:                        05:49:05   Log-Likelihood:                 129.76
No. Observations:                  28   AIC:                            -253.5
Df Residuals:                      25   BIC:                            -249.5
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const               0.0123      0.000     25.928      0.000       0.011       0.013
NSE ASI             0.0143      0.008      1.722      0.097      -0.003       0.031
12yr-Bond Yield    -0.0089      0.018     -0.497      0.624      -0.046       0.028
==============================================================================
Omnibus:                        1.166   Durbin-Watson:                   0.868
Prob(Omnibus):                  0.558   Jarque-Bera (JB):                0.961
Skew:                          -0.431   Prob(JB):                        0.619
Kurtosis:                       2.716   Cond. No.                         39.0
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

###### Balanced Portfolio

In [29]:
Y3 = data['Balanced']                               # Dependent variable
X1c = sm.add_constant(X1)
reg3 = sm.OLS(Y3, X1c).fit()
#prediction1 = reg1.predict(X1)

reg3.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               Balanced   R-squared:                       0.657
Model:                            OLS   Adj. R-squared:                  0.073
Method:                 Least Squares   F-statistic:                     1.126
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.438
Time:                        05:49:05   Log-Likelihood:                 142.29
No. Observations:                  28   AIC:                            -248.6
Df Residuals:                      10   BIC:                            -224.6
Df Model:                          17                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const               0.0115      0.001     17.171      0.000       0.010       0.013
Oil Prices          0.0030      0.010      0.304      0.768      -0.019       0.025
Inflation           0.0037      0.022      0.168      0.870      -0.045       0.053
NSE ASI             0.0202      0.009      2.158      0.056      -0.001       0.041
FX Reserves         0.0230      0.016      1.475      0.171      -0.012       0.058
USD/NGN (BDC)      -0.0266      0.014     -1.899      0.087      -0.058       0.005
USD/NGN (I&E)       0.0138      0.013      1.084      0.304      -0.015       0.042
91-Day Yield        0.0020      0.007      0.306      0.766      -0.013       0.017
182-Day Yield      -0.0006      0.012     -0.051      0.960      -0.026       0.025
364-Day Yield      -0.0066      0.015     -0.445      0.666      -0.039       0.026
2yr-Bond Yield     -0.0167      0.019     -0.899      0.390      -0.058       0.025
3yr-Bond Yield      0.0211      0.038      0.553      0.592      -0.064       0.106
5yr-Bond Yield      0.0477      0.059      0.803      0.441      -0.085       0.180
7yr-Bond Yield     -0.1057      0.089     -1.192      0.261      -0.303       0.092
10yr-Bond Yield    -0.0191      0.107     -0.178      0.863      -0.258       0.220
12yr-Bond Yield     0.0815      0.198      0.412      0.689      -0.359       0.522
15yr-Bond Yield    -0.0340      0.139     -0.245      0.812      -0.344       0.276
20yr-Bond Yield     0.0360      0.072      0.497      0.630      -0.125       0.197
==============================================================================
Omnibus:                        2.850   Durbin-Watson:                   2.133
Prob(Omnibus):                  0.240   Jarque-Bera (JB):                1.663
Skew:                           0.572   Prob(JB):                        0.435
Kurtosis:                       3.340   Cond. No.                         514.
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [30]:
# Some independent variables exhibited a relationship with the dependent variable 
# (Balanced Portfolio). Re-ran the regression with the variables.

X1_bal = data[['5yr-Bond Yield', '12yr-Bond Yield', '15yr-Bond Yield']]     # Indepedent variable
Y3_bal = data['Balanced']                                                   # Dependent variable
X1b_bal = sm.add_constant(X1_bal)
reg3_bal = sm.OLS(Y3_bal, X1b_bal).fit()
#prediction1 = reg1.predict(X1)

reg3_bal.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               Balanced   R-squared:                       0.084
Model:                            OLS   Adj. R-squared:                 -0.030
Method:                 Least Squares   F-statistic:                    0.7382
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.540
Time:                        05:49:06   Log-Likelihood:                 128.55
No. Observations:                  28   AIC:                            -249.1
Df Residuals:                      24   BIC:                            -243.8
Df Model:                           3                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const               0.0124      0.001     24.585      0.000       0.011       0.013
5yr-Bond Yield      0.0325      0.044      0.735      0.469      -0.059       0.124
12yr-Bond Yield    -0.0749      0.086     -0.874      0.391      -0.252       0.102
15yr-Bond Yield     0.0229      0.074      0.308      0.761      -0.131       0.177
==============================================================================
Omnibus:                        0.567   Durbin-Watson:                   0.694
Prob(Omnibus):                  0.753   Jarque-Bera (JB):                0.631
Skew:                          -0.291   Prob(JB):                        0.730
Kurtosis:                       2.550   Cond. No.                         220.
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

###### Growth Portfolio

In [31]:
Y4 = data['Growth']                                  # Dependent variable
X1d = sm.add_constant(X1)
reg4 = sm.OLS(Y4, X1d).fit()
#prediction1 = reg1.predict(X1)

reg4.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                 Growth   R-squared:                       0.874
Model:                            OLS   Adj. R-squared:                  0.659
Method:                 Least Squares   F-statistic:                     4.075
Date:                Sun, 28 Jun 2020   Prob (F-statistic):             0.0142
Time:                        05:49:06   Log-Likelihood:                 100.12
No. Observations:                  28   AIC:                            -164.2
Df Residuals:                      10   BIC:                            -140.3
Df Model:                          17                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const               0.0063      0.003      2.068      0.065      -0.000       0.013
Oil Prices          0.0179      0.044      0.407      0.693      -0.080       0.116
Inflation          -0.0518      0.099     -0.520      0.614      -0.273       0.170
NSE ASI             0.2627      0.042      6.220      0.000       0.169       0.357
FX Reserves        -0.0136      0.070     -0.194      0.850      -0.171       0.143
USD/NGN (BDC)      -0.0095      0.063     -0.151      0.883      -0.150       0.131
USD/NGN (I&E)       0.0859      0.057      1.501      0.164      -0.042       0.213
91-Day Yield        0.0026      0.030      0.087      0.933      -0.064       0.069
182-Day Yield      -0.0086      0.052     -0.166      0.872      -0.125       0.108
364-Day Yield      -0.0657      0.067     -0.987      0.347      -0.214       0.083
2yr-Bond Yield     -0.0825      0.084     -0.983      0.349      -0.270       0.105
3yr-Bond Yield     -0.0353      0.172     -0.205      0.842      -0.418       0.348
5yr-Bond Yield     -0.0374      0.268     -0.140      0.892      -0.635       0.560
7yr-Bond Yield     -0.0265      0.400     -0.066      0.948      -0.918       0.865
10yr-Bond Yield     0.4843      0.484      1.000      0.341      -0.595       1.563
12yr-Bond Yield     0.0156      0.891      0.018      0.986      -1.970       2.001
15yr-Bond Yield     0.1068      0.627      0.170      0.868      -1.290       1.504
20yr-Bond Yield    -0.3583      0.326     -1.098      0.298      -1.085       0.369
==============================================================================
Omnibus:                        6.384   Durbin-Watson:                   3.153
Prob(Omnibus):                  0.041   Jarque-Bera (JB):                5.207
Skew:                          -0.598   Prob(JB):                       0.0740
Kurtosis:                       4.741   Cond. No.                         514.
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [32]:
# Some independent variables exhibited a relationship with the dependent variable 
# (Growth Portfolio). Re-ran the regression with the variables.

X1_grow = data[['Inflation', '2yr-Bond Yield']]     # Indepedent variable
Y4_grow = data['Balanced']                                                    # Dependent variable
X1b_grow = sm.add_constant(X1_grow)
reg4_grow = sm.OLS(Y4_grow, X1b_grow).fit()
#prediction1 = reg1.predict(X1)

reg4_grow.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               Balanced   R-squared:                       0.088
Model:                            OLS   Adj. R-squared:                  0.015
Method:                 Least Squares   F-statistic:                     1.208
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.316
Time:                        05:49:06   Log-Likelihood:                 128.61
No. Observations:                  28   AIC:                            -251.2
Df Residuals:                      25   BIC:                            -247.2
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
==================================================================================
                     coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------
const              0.0120      0.001     21.645      0.000       0.011       0.013
Inflation         -0.0168      0.017     -0.958      0.347      -0.053       0.019
2yr-Bond Yield    -0.0126      0.011     -1.192      0.244      -0.034       0.009
==============================================================================
Omnibus:                        1.012   Durbin-Watson:                   0.694
Prob(Omnibus):                  0.603   Jarque-Bera (JB):                0.928
Skew:                          -0.242   Prob(JB):                        0.629
Kurtosis:                       2.251   Cond. No.                         35.7
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

###### Aggressive Portfolio

In [33]:
Y5 = data['Aggressive']                               # Dependent variable
X1e = sm.add_constant(X1)
reg5 = sm.OLS(Y5, X1e).fit()
#prediction1 = reg1.predict(X1)

reg5.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:             Aggressive   R-squared:                       0.860
Model:                            OLS   Adj. R-squared:                  0.623
Method:                 Least Squares   F-statistic:                     3.619
Date:                Sun, 28 Jun 2020   Prob (F-statistic):             0.0217
Time:                        05:49:06   Log-Likelihood:                 82.632
No. Observations:                  28   AIC:                            -129.3
Df Residuals:                      10   BIC:                            -105.3
Df Model:                          17                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const               0.0019      0.006      0.328      0.749      -0.011       0.014
Oil Prices          0.0306      0.082      0.371      0.718      -0.153       0.214
Inflation          -0.0982      0.186     -0.528      0.609      -0.512       0.316
NSE ASI             0.4604      0.079      5.836      0.000       0.285       0.636
FX Reserves        -0.0433      0.132     -0.329      0.749      -0.336       0.250
USD/NGN (BDC)       0.0054      0.118      0.046      0.964      -0.258       0.269
USD/NGN (I&E)       0.1441      0.107      1.348      0.207      -0.094       0.382
91-Day Yield        0.0028      0.056      0.051      0.960      -0.121       0.127
182-Day Yield      -0.0156      0.098     -0.160      0.876      -0.233       0.202
364-Day Yield      -0.1130      0.124     -0.908      0.385      -0.390       0.164
2yr-Bond Yield     -0.1347      0.157     -0.859      0.411      -0.484       0.215
3yr-Bond Yield     -0.0813      0.321     -0.253      0.805      -0.797       0.634
5yr-Bond Yield     -0.1126      0.501     -0.225      0.827      -1.228       1.003
7yr-Bond Yield      0.0499      0.747      0.067      0.948      -1.615       1.714
10yr-Bond Yield     0.8966      0.904      0.991      0.345      -1.119       2.912
12yr-Bond Yield    -0.0402      1.664     -0.024      0.981      -3.749       3.668
15yr-Bond Yield     0.2206      1.171      0.188      0.854      -2.389       2.830
20yr-Bond Yield    -0.6874      0.609     -1.128      0.285      -2.045       0.670
==============================================================================
Omnibus:                        5.027   Durbin-Watson:                   3.120
Prob(Omnibus):                  0.081   Jarque-Bera (JB):                3.517
Skew:                          -0.522   Prob(JB):                        0.172
Kurtosis:                       4.388   Cond. No.                         514.
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [34]:
# Some independent variables exhibited a relationship with the dependent variable 
# (Dollar Portfolio). Re-ran the regression with the variables.

X1_aggres = data[['Inflation', '2yr-Bond Yield']]     # Indepedent variable
Y5_aggres = data['Balanced']                          # Dependent variable
X1b_aggres = sm.add_constant(X1_aggres)
reg5_aggres = sm.OLS(Y5_aggres, X1b_aggres).fit()
#prediction1 = reg1.predict(X1)

reg5_aggres.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               Balanced   R-squared:                       0.088
Model:                            OLS   Adj. R-squared:                  0.015
Method:                 Least Squares   F-statistic:                     1.208
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.316
Time:                        05:49:06   Log-Likelihood:                 128.61
No. Observations:                  28   AIC:                            -251.2
Df Residuals:                      25   BIC:                            -247.2
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
==================================================================================
                     coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------
const              0.0120      0.001     21.645      0.000       0.011       0.013
Inflation         -0.0168      0.017     -0.958      0.347      -0.053       0.019
2yr-Bond Yield    -0.0126      0.011     -1.192      0.244      -0.034       0.009
==============================================================================
Omnibus:                        1.012   Durbin-Watson:                   0.694
Prob(Omnibus):                  0.603   Jarque-Bera (JB):                0.928
Skew:                          -0.242   Prob(JB):                        0.629
Kurtosis:                       2.251   Cond. No.                         35.7
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [35]:
Y6 = data['Dollar']                                   # Dependent variable
X1f = sm.add_constant(X1)
reg6 = sm.OLS(Y6, X1f).fit()
#prediction1 = reg1.predict(X1)

reg6.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                 Dollar   R-squared:                       0.599
Model:                            OLS   Adj. R-squared:                 -0.083
Method:                 Least Squares   F-statistic:                    0.8784
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.609
Time:                        05:49:06   Log-Likelihood:                 116.23
No. Observations:                  28   AIC:                            -196.5
Df Residuals:                      10   BIC:                            -172.5
Df Model:                          17                                         
Covariance Type:            nonrobust                                         
===================================================================================
                      coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------
const               0.0016      0.002      0.921      0.379      -0.002       0.005
Oil Prices          0.0131      0.025      0.526      0.610      -0.042       0.068
Inflation          -0.0578      0.056     -1.034      0.326      -0.183       0.067
NSE ASI             0.0350      0.024      1.474      0.171      -0.018       0.088
FX Reserves         0.0170      0.040      0.428      0.678      -0.071       0.105
USD/NGN (BDC)       0.0147      0.036      0.413      0.689      -0.065       0.094
USD/NGN (I&E)       0.0231      0.032      0.718      0.489      -0.049       0.095
91-Day Yield        0.0025      0.017      0.149      0.884      -0.035       0.040
182-Day Yield       0.0220      0.029      0.750      0.471      -0.043       0.087
364-Day Yield       0.0258      0.037      0.689      0.507      -0.058       0.109
2yr-Bond Yield      0.0018      0.047      0.037      0.971      -0.104       0.107
3yr-Bond Yield     -0.0034      0.097     -0.036      0.972      -0.219       0.212
5yr-Bond Yield      0.0764      0.151      0.507      0.623      -0.260       0.412
7yr-Bond Yield      0.0379      0.225      0.169      0.869      -0.463       0.539
10yr-Bond Yield    -0.4285      0.272     -1.573      0.147      -1.035       0.178
12yr-Bond Yield     0.3311      0.501      0.660      0.524      -0.786       1.448
15yr-Bond Yield    -0.0400      0.353     -0.113      0.912      -0.826       0.746
20yr-Bond Yield    -0.0477      0.183     -0.260      0.800      -0.457       0.361
==============================================================================
Omnibus:                        3.245   Durbin-Watson:                   1.947
Prob(Omnibus):                  0.197   Jarque-Bera (JB):                1.899
Skew:                          -0.597   Prob(JB):                        0.387
Kurtosis:                       3.453   Cond. No.                         514.
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [36]:
# Some independent variables exhibited a relationship with the dependent variable 
# (Dollar Portfolio). Re-ran the regression with the variables.

X1_doll = data[['USD/NGN (I&E)', '2yr-Bond Yield', '5yr-Bond Yield']]   # Indepedent variable
Y6_doll = data['Balanced']                                              # Dependent variable
X1b_doll = sm.add_constant(X1_doll)
reg6_doll = sm.OLS(Y6_doll, X1b_doll).fit()
#prediction1 = reg1.predict(X1)

reg6_doll.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:               Balanced   R-squared:                       0.108
Model:                            OLS   Adj. R-squared:                 -0.004
Method:                 Least Squares   F-statistic:                    0.9658
Date:                Sun, 28 Jun 2020   Prob (F-statistic):              0.425
Time:                        05:49:07   Log-Likelihood:                 128.91
No. Observations:                  28   AIC:                            -249.8
Df Residuals:                      24   BIC:                            -244.5
Df Model:                           3                                         
Covariance Type:            nonrobust                                         
==================================================================================
                     coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------------
const              0.0122      0.001     23.713      0.000       0.011       0.013
USD/NGN (I&E)      0.0135      0.012      1.170      0.253      -0.010       0.037
2yr-Bond Yield    -0.0116      0.013     -0.880      0.388      -0.039       0.016
5yr-Bond Yield    -0.0076      0.021     -0.368      0.716      -0.050       0.035
==============================================================================
Omnibus:                        1.674   Durbin-Watson:                   0.766
Prob(Omnibus):                  0.433   Jarque-Bera (JB):                1.262
Skew:                          -0.512   Prob(JB):                        0.532
Kurtosis:                       2.818   Cond. No.                         45.2
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

### Monte Carlo Simulation

In [37]:
# Calculate percentage returns from monthly asset returns

stb_etf_returns = (new_prices['Stanbic ETF 30'].div(new_prices.groupby('year month')['Stanbic ETF 30'].shift(1)) - 1).dropna().reset_index(drop = True)
stb_abs_returns = (new_prices['Stanbic Absolute Fund'].div(new_prices.groupby('year month')['Stanbic Absolute Fund'].shift(1)) - 1).dropna().reset_index(drop = True)
stb_gtd_returns = (new_prices['Stanbic Guaranteed Income Fund'].div(new_prices.groupby('year month')['Stanbic Guaranteed Income Fund'].shift(1)) - 1).dropna().reset_index(drop = True)
stb_euro_returns = (new_prices['Stanbic Eurobond Fund'].div(new_prices.groupby('year month')['Stanbic Eurobond Fund'].shift(1)) - 1).dropna().reset_index(drop = True)
fbn_euro_returns = (new_prices['FBN Eurobond Fund'].div(new_prices.groupby('year month')['FBN Eurobond Fund'].shift(1)) - 1).dropna().reset_index(drop = True)

In [38]:
#dates1 = pd.date_range(start = '08-01-2016', periods = 55, freq = 'M')
dates.to_period('M')

PeriodIndex(['2016-08', '2016-09', '2016-10', '2016-11', '2016-12', '2017-01',
             '2017-02', '2017-03', '2017-04', '2017-05', '2017-06', '2017-07',
             '2017-08', '2017-09', '2017-10', '2017-11', '2017-12', '2018-01',
             '2018-02', '2018-03', '2018-04', '2018-05', '2018-06', '2018-07',
             '2018-08', '2018-09', '2018-10', '2018-11'],
            dtype='period[M]', freq='M')

In [39]:
# Create a dataframe from log returns of asset

month_returns_log = pd.DataFrame({'Date': dates.to_period('M'), 
                                  'Stanbic ETF 30': stb_etf_returns, 
                                  'Stanbic Absolute Fund': stb_abs_returns, 
                                  'Stanbic Guaranteed Income Fund': stb_gtd_returns, 
                                  'Stanbic Eurobond Fund': stb_euro_returns, 
                                  'FBN Eurobond Fund': fbn_euro_returns, 
                                 'AXA Money Market Fund Yield': axa_mmf_['AXA Money Market Fund Yield']})

In [40]:
# Calculate the average return of each asset

stb_etf_mean = np.array(month_returns_log['Stanbic ETF 30'].mean())
stb_abs_mean = np.array(month_returns_log['Stanbic Absolute Fund'].mean())
stb_gtb_mean = np.array(month_returns_log['Stanbic Guaranteed Income Fund'].mean())
stb_euro_mean = np.array(month_returns_log['Stanbic Eurobond Fund'].mean())
fbn_euro_mean = np.array(month_returns_log['FBN Eurobond Fund'].mean())
axa_mmf_mean = np.array(month_returns_log['AXA Money Market Fund Yield'].mean())

In [41]:
# Calculate the variance of each asset

stb_etf_var = np.array(month_returns_log['Stanbic ETF 30'].var())
stb_abs_var = np.array(month_returns_log['Stanbic Absolute Fund'].var())
stb_gtb_var = np.array(month_returns_log['Stanbic Guaranteed Income Fund'].var())
stb_euro_var = np.array(month_returns_log['Stanbic Eurobond Fund'].var())
fbn_euro_var = np.array(month_returns_log['FBN Eurobond Fund'].var())
axa_mmf_var = np.array(month_returns_log['AXA Money Market Fund Yield'].var())

In [42]:
# Calculate the standard deviation of each asset

stb_etf_std = np.array(month_returns_log['Stanbic ETF 30'].std())
stb_abs_std = np.array(month_returns_log['Stanbic Absolute Fund'].std())
stb_gtb_std = np.array(month_returns_log['Stanbic Guaranteed Income Fund'].std())
stb_euro_std = np.array(month_returns_log['Stanbic Eurobond Fund'].std())
fbn_euro_std = np.array(month_returns_log['FBN Eurobond Fund'].std())
axa_mmf_std = np.array(month_returns_log['AXA Money Market Fund Yield'].std())

In [43]:
# Calculate the drift of each asset

stb_etf_drift = np.array(stb_etf_mean - ( 0.5 * stb_etf_var))
stb_abs_drift = np.array(stb_abs_mean - ( 0.5 * stb_abs_var))
stb_gtb_drift = np.array(stb_gtb_mean - ( 0.5 * stb_gtb_var))
stb_euro_drift = np.array(stb_euro_mean - ( 0.5 * stb_euro_var))
fbn_euro_drift = np.array(fbn_euro_mean - ( 0.5 * fbn_euro_var))
axa_mmf_drift = np.array(axa_mmf_mean - ( 0.5 * axa_mmf_var))

In [44]:
t_intervals = 1200
n_iterations = 1000

In [45]:
# Calculates the predicted returns using the Brownian Motion for Fianacial Markets model

stb_etf_pred = (np.exp(stb_etf_drift + stb_etf_std * norm.ppf(np.random.rand(t_intervals, n_iterations))) - 1)
stb_abs_pred = (np.exp(stb_abs_drift + stb_abs_std * norm.ppf(np.random.rand(t_intervals, n_iterations))) - 1)
stb_gtb_pred = (np.exp(stb_gtb_drift + stb_gtb_std * norm.ppf(np.random.rand(t_intervals, n_iterations))) - 1)
stb_euro_pred = (np.exp(stb_euro_drift + stb_euro_std * norm.ppf(np.random.rand(t_intervals, n_iterations))) - 1)
fbn_euro_pred = (np.exp(fbn_euro_drift + fbn_euro_std * norm.ppf(np.random.rand(t_intervals, n_iterations))) - 1)
axa_mmf_pred = (np.exp(axa_mmf_drift + axa_mmf_std * norm.ppf(np.random.rand(t_intervals, n_iterations))) - 1)

In [46]:
# Convert numpy array of asset returns to dataframe

stb_etf_pred = pd.DataFrame(data = stb_etf_pred[:,:])
stb_abs_pred = pd.DataFrame(data = stb_abs_pred[:,:])
stb_gtb_pred = pd.DataFrame(data = stb_gtb_pred[:,:])
stb_euro_pred = pd.DataFrame(data = stb_euro_pred[:,:])
fbn_euro_pred = pd.DataFrame(data = fbn_euro_pred[:,:])
axa_mmf_pred = pd.DataFrame(data = axa_mmf_pred[:,:])

In [47]:
# Extract month feature from date

dates = pd.date_range(start = '01-01-2019', periods = 1200, freq = 'M')
dates.to_period('M')
index = 0

#### Conservative Portfolio Simulation

In [48]:
# Calculates portfolio expected returns from the portfolio ratios and the predicted returns
# Extracts year and month from the date

stb_a = stb_abs_pred * stb_abs1
axa_a = axa_mmf_pred * axa_mmf1

conserv = stb_a.add(axa_a)
conserv.insert(loc = index, column = 'Year', value = dates.to_period('Y'))
conserv.insert(loc = index, column = 'Date', value = dates.to_period('M'))
conserv.head()

Date  Year         0         1         2         3         4         5  \
0  2019-01  2019  0.010476  0.011499  0.012970  0.008271  0.011176  0.013083   
1  2019-02  2019  0.011904  0.009286  0.012738  0.011299  0.012930  0.015306   
2  2019-03  2019  0.011620  0.012798  0.008831  0.011637  0.010332  0.010174   
3  2019-04  2019  0.014624  0.008790  0.008516  0.014966  0.009617  0.010602   
4  2019-05  2019  0.011013  0.015939  0.009515  0.013127  0.010992  0.014704   

          6         7         8         9        10        11        12  \
0  0.011887  0.016546  0.009263  0.016360  0.011925  0.007766  0.011345   
1  0.010533  0.012912  0.011338  0.007896  0.012933  0.010678  0.010661   
2  0.016729  0.014576  0.010342  0.018515  0.013219  0.014138  0.009354   
3  0.017531  0.011200  0.010962  0.012608  0.008887  0.013732  0.010953   
4  0.010553  0.011418  0.011400  0.012263  0.014484  0.009702  0.010574   

         13        14        15        16        17        18        19  \
0  0.016662  0.007177  0.009507  0.011282  0.013775  0.011280  0.013599   
1  0.013868  0.007761  0.010171  0.015382  0.013527  0.011897  0.007003   
2  0.012371  0.011327  0.011434  0.010242  0.016819  0.011435  0.011251   
3  0.012065  0.012860  0.016989  0.010382  0.012817  0.013074  0.012667   
4  0.013116  0.010412  0.014278  0.016137  0.009704  0.013396  0.011905   

         20        21        22        23        24        25        26  \
0  0.009406  0.011518  0.009424  0.010089  0.012896  0.010186  0.010329   
1  0.014346  0.013877  0.013254  0.011586  0.011076  0.011009  0.011241   
2  0.012097  0.007445  0.014199  0.009892  0.012095  0.009055  0.009534   
3  0.011852  0.009893  0.010049  0.011867  0.012143  0.012677  0.013340   
4  0.010328  0.010452  0.008579  0.015950  0.011047  0.011556  0.013074   

         27        28        29        30        31        32        33  \
0  0.011198  0.013586  0.011838  0.014245  0.013136  0.013729  0.010265   
1  0.011236  0.009704  0.011401  0.014798  0.014087  0.011759  0.011117   
2  0.014444  0.012874  0.012924  0.010455  0.008437  0.012156  0.008268   
3  0.008181  0.010351  0.009882  0.011865  0.008852  0.014390  0.010781   
4  0.015349  0.011982  0.012053  0.010191  0.011782  0.010776  0.013657   

         34        35        36        37        38        39        40  \
0  0.011038  0.009675  0.012293  0.015983  0.014303  0.013743  0.010437   
1  0.014753  0.012984  0.009765  0.014367  0.011214  0.014809  0.007459   
2  0.011741  0.011643  0.009362  0.011607  0.010798  0.014720  0.012240   
3  0.012944  0.012458  0.012335  0.008700  0.014193  0.011752  0.020320   
4  0.013487  0.011868  0.009597  0.010724  0.012757  0.011171  0.011369   

         41        42        43        44        45        46        47  \
0  0.013398  0.006449  0.007753  0.009791  0.012372  0.012567  0.012899   
1  0.010860  0.015731  0.013468  0.006828  0.015068  0.009617  0.013065   
2  0.008040  0.010234  0.015351  0.011229  0.007035  0.012988  0.011436   
3  0.006662  0.011907  0.009281  0.010426  0.012165  0.010366  0.014105   
4  0.008556  0.015526  0.007895  0.014171  0.012578  0.010890  0.008822   

         48        49        50        51        52        53        54  \
0  0.010954  0.013004  0.009673  0.015048  0.008800  0.012993  0.010074   
1  0.010676  0.011512  0.010411  0.013412  0.012558  0.015101  0.011577   
2  0.010996  0.011317  0.014282  0.013424  0.013232  0.009797  0.016190   
3  0.011425  0.013276  0.009991  0.007021  0.011812  0.013386  0.011720   
4  0.014097  0.013793  0.010219  0.013419  0.011972  0.012356  0.008996   

         55        56        57        58        59        60        61  \
0  0.012019  0.010133  0.012190  0.014733  0.012353  0.010507  0.008916   
1  0.012834  0.012357  0.009174  0.015597  0.014951  0.011739  0.009069   
2  0.012090  0.009566  0.012996  0.013101  0.008260  0.012265  0.014642   
3  0.012028  0.010597  0.012222  0.010296  0.009567  0.013838  0.010

In [49]:
#Calculates the nominal returns

conserv_ret = pd.concat([conserv['Date'], conserv['Year'], (conserv[list(range(0, 1000))] * 100000)], axis = 1)
conserv_df = conserv_ret.copy()
conserv_nom = conserv_df.drop(columns = ['Year'], axis  = 1)
conserv_nom.head()

Date            0            1            2            3            4  \
0  2019-01  1047.619369  1149.904991  1296.964235   827.114134  1117.571120   
1  2019-02  1190.399666   928.575298  1273.835203  1129.892418  1292.959337   
2  2019-03  1162.039251  1279.844984   883.149103  1163.656501  1033.234216   
3  2019-04  1462.383505   878.980184   851.554790  1496.552444   961.707615   
4  2019-05  1101.330999  1593.890526   951.548328  1312.742338  1099.159815   

             5            6            7            8            9  \
0  1308.349891  1188.691697  1654.577466   926.332214  1635.992836   
1  1530.619953  1053.273205  1291.156173  1133.816847   789.592055   
2  1017.433786  1672.860719  1457.641833  1034.159894  1851.529828   
3  1060.202300  1753.133934  1119.968120  1096.185225  1260.786502   
4  1470.436193  1055.348859  1141.771413  1140.013368  1226.282573   

            10           11           12           13           14  \
0  1192.486159   776.630905  1134.500556  1666.158769   717.661624   
1  1293.325733  1067.848379  1066.051830  1386.839810   776.079371   
2  1321.933717  1413.817038   935.412863  1237.143713  1132.660319   
3   888.745937  1373.211586  1095.278086  1206.474337  1286.041218   
4  1448.424803   970.191033  1057.354968  1311.635939  1041.205924   

            15           16           17           18           19  \
0   950.711461  1128.221447  1377.480413  1128.012731  1359.941768   
1  1017.057729  1538.151267  1352.747634  1189.728789   700.312492   
2  1143.404646  1024.221549  1681.926752  1143.497043  1125.092949   
3  1698.877384  1038.182850  1281.672709  1307.360183  1266.702568   
4  1427.751092  1613.665868   970.429924  1339.592470  1190.491778   

            20           21           22           23           24  \
0   940.611717  1151.787376   942.386759  1008.910114  1289.579960   
1  1434.621960  1387.657727  1325.365198  1158.637988  1107.588460   
2  1209.653839   744.467380  1419.942243   989.233719  1209.507848   
3  1185.176876   989.295598  1004.893940  1186.682262  1214.309122   
4  1032.750572  1045.243789   857.936818  1595.004120  1104.679582   

            25           26           27           28           29  \
0  1018.605801  1032.928368  1119.781084  1358.591197  1183.818934   
1  1100.942724  1124.051228  1123.629431   970.411189  1140.066416   
2   905.468675   953.379353  1444.350708  1287.408226  1292.372460   
3  1267.744725  1333.977299   818.118211  1035.092973   988.219079   
4  1155.578796  1307.423725  1534.930518  1198.202035  1205.328843   

            30           31           32           33           34  \
0  1424.473916  1313.574053  1372.915751  1026.471395  1103.840507   
1  1479.842364  1408.708301  1175.927337  1111.715187  1475.338900   
2  1045.518295   843.672680  1215.582913   826.771903  1174.107286   
3  1186.510749   885.202903  1438.953786  1078.109358  1294.441204   
4  1019.060147  1178.225999  1077.639529  1365.673488  1348.744248   

            35           36           37           38           39  \
0   967.496702  1229.288362  1598.250267  1430.346489  1374.272060   
1  1298.400836   976.485543  1436.740554  1121.412894  1480.853483   
2  1164.316805   936.156701  1160.668157  1079.795739  1471.959731   
3  1245.818277  1233.500864   870.044601  1419.250375  1175.214535   
4  1186.812029   959.749009  1072.414589  1275.692053  1117.146556   

            40           41           42           43           44  \
0  1043.686175  1339.750420   644.859216   775.320821   979.133378   
1   745.924618  1085.976519  1573.104330  1346.844051   682.756281   
2  1223.974780   803.950035  1023.426196  1535.076020  1122.859070   
3  2031.995065   666.210346  1190.690979   928.067624  1042.617396   
4  1136.915589   855.600510  1552.648372   789.537945  1417.119789   

            45           46           47           48           49  \
0  1237.208525  1256.728607  1289.897160  1095.352118  1300.409597   
1  1506.781759   961.72

In [50]:
# Calculates the cummulative monthly returns

conserv_mth = conserv_ret.drop(columns = ['Year'], axis = 1)
conserv_mth.iloc[:1, 1:] = conserv_mth.iloc[:1, 1:] + 100000
conserv_mth = round(conserv_mth, 3)
conserv_mth.iloc[:, 1:] = conserv_mth.iloc[:, 1:].cumsum()
conserv_mth.head()

Date           0           1           2           3           4  \
0  2019-01  101047.619  101149.905  101296.964  100827.114  101117.571   
1  2019-02  102238.019  102078.480  102570.799  101957.006  102410.530   
2  2019-03  103400.058  103358.325  103453.948  103120.663  103443.764   
3  2019-04  104862.442  104237.305  104305.503  104617.215  104405.472   
4  2019-05  105963.773  105831.196  105257.051  105929.957  105504.632   

            5           6           7           8           9          10  \
0  101308.350  101188.692  101654.577  100926.332  101635.993  101192.486   
1  102838.970  102241.965  102945.733  102060.149  102425.585  102485.812   
2  103856.404  103914.826  104403.375  103094.309  104277.115  103807.746   
3  104916.606  105667.960  105523.343  104190.494  105537.902  104696.492   
4  106387.042  106723.309  106665.114  105330.507  106764.185  106144.917   

           11          12          13          14          15          16  \
0  100776.631  101134.501  101666.159  100717.662  100950.711  101128.221   
1  101844.479  102200.553  103052.999  101493.741  101967.769  102666.372   
2  103258.296  103135.966  104290.143  102626.401  103111.174  103690.594   
3  104631.508  104231.244  105496.617  103912.442  104810.051  104728.777   
4  105601.699  105288.599  106808.253  104953.648  106237.802  106342.443   

           17          18          19          20          21          22  \
0  101377.480  101128.013  101359.942  100940.612  101151.787  100942.387   
1  102730.228  102317.742  102060.254  102375.234  102539.445  102267.752   
2  104412.155  103461.239  103185.347  103584.888  103283.912  103687.694   
3  105693.828  104768.599  104452.050  104770.065  104273.208  104692.588   
4  106664.258  106108.191  105642.542  105802.816  105318.452  105550.525   

           23          24          25          26          27          28  \
0  101008.910  101289.580  101018.606  101032.928  101119.781  101358.591   
1  102167.548  102397.168  102119.549  102156.979  102243.410  102329.002   
2  103156.782  103606.676  103025.018  103110.358  103687.761  103616.410   
3  104343.464  104820.985  104292.763  104444.335  104505.879  104651.503   
4  105938.468  105925.665  105448.342  105751.759  106040.810  105849.705   

           29          30          31          32          33          34  \
0  101183.819  101424.474  101313.574  101372.916  101026.471  101103.841   
1  102323.885  102904.316  102722.282  102548.843  102138.186  102579.180   
2  103616.257  103949.834  103565.955  103764.426  102964.958  103753.287   
3  104604.476  105136.345  104451.158  105203.380  104043.067  105047.728   
4  105809.805  106155.405  105629.384  106281.020  105408.740  106396.472   

           35          36          37          38          39          40  \
0  100967.497  101229.288  101598.250  101430.346  101374.272  101043.686   
1  102265.898  102205.774  103034.991  102551.759  102855.125  101789.611   
2  103430.215  103141.931  104195.659  103631.555  104327.085  103013.586   
3  104676.033  104375.432  105065.704  105050.805  105502.300  105045.581   
4  105862.845  105335.181  106138.119  106326.497  106619.447  106182.497   

           41          42          43          44          45          46  \
0  101339.750  100644.859  100775.321  100979.133  101237.209  101256.729   
1  102425.727  102217.963  102122.165  101661.889  102743.991  102218.450   
2  103229.677  103241.389  103657.241  102784.748  103447.537  103517.276   
3  103895.887  104432.080  104585.309  103827.365  104663.998  104553.926   
4  104751.488  105984.728  105374.847  105244.485  105921.767  105642.969   

           47          48          49          50          51          52  \
0  101289.897  101095.352  101300.410  100967.344  101504.827  100879.974   
1  102596.375  102162.940  102451.610  102008.442  102845.984  102135.767   
2  103739.968  103262.526  103583.271  103436.635  104188.374  103458.953   
3  105150.46

In [51]:
# Calculates the cummulative yearly returns

conserv_port = conserv_ret.groupby('Year').sum().reset_index()
conserv_port.iloc[:1, 1:] = conserv_port.iloc[:1, 1:].apply(lambda x: x + 100000)
conserv_port = round(conserv_port, 3)
conserv_port.iloc[:, 1:] = conserv_port.iloc[:, 1:].cumsum()
conserv_port.head()

Year           0           1           2           3           4  \
0  2019  114185.000  113658.984  113678.393  114516.625  114245.883   
1  2020  127743.929  127315.150  128740.653  128039.961  128654.506   
2  2021  141630.643  140579.237  142645.781  141316.391  142732.236   
3  2022  156476.699  154638.816  155399.846  155788.196  155965.796   
4  2023  170292.151  168182.755  167360.188  170587.994  170642.128   

            5           6           7           8           9          10  \
0  113863.717  113675.109  115687.871  114032.003  116436.311  113828.233   
1  126543.108  128108.918  130348.722  128081.590  130824.849  127483.672   
2  140871.679  143458.273  143911.232  142797.878  146630.799  141644.634   
3  154836.769  157443.991  157566.334  157456.464  160931.874  156826.800   
4  169920.819  170222.742  171495.593  172408.951  174646.399  171058.684   

           11          12          13          14          15          16  \
0  113797.882  114165.465  114820.040  112831.515  113807.485  113676.346   
1  126771.212  127804.734  128403.068  127455.063  127757.537  127684.780   
2  140896.405  143271.473  142509.082  140717.309  140863.093  140701.748   
3  154990.589  156346.380  156701.077  154586.375  155776.283  154739.591   
4  169547.718  169950.768  169899.991  168538.547  167847.885  167956.862   

           17          18          19          20          21          22  \
0  114090.266  114197.284  113063.723  113768.366  114148.884  113854.442   
1  127442.414  128511.141  128381.772  128084.546  126775.446  127388.482   
2  142754.640  142316.550  141898.813  141886.154  141192.245  141070.836   
3  156639.016  155834.017  154605.609  156959.662  155964.710  154775.980   
4  169690.204  169753.322  168248.863  171014.320  169938.763  168722.288   

           23          24          25          26          27          28  \
0  114201.838  113845.025  113976.457  113867.776  115573.949  114957.033   
1  128105.285  128352.365  127532.726  127746.552  129446.587  129388.952   
2  142259.130  141484.330  142684.388  143395.724  143824.793  143453.958   
3  156916.533  155041.163  156806.021  157109.036  157767.349  156734.676   
4  170061.360  168438.891  171375.885  170879.293  172944.792  170225.719   

           29          30          31          32          33          34  \
0  113766.284  115053.397  113515.581  114318.073  113339.842  115913.500   
1  127357.945  129129.339  125944.559  129077.684  126935.779  130031.734   
2  142420.349  142629.258  139034.629  144055.149  140994.182  142560.634   
3  157277.132  156320.583  154368.523  158366.308  155230.726  157007.774   
4  170845.187  170605.870  168381.757  172813.657  169964.657  170103.072   

           35          36          37          38          39          40  \
0  114160.965  112575.967  114483.593  115523.928  114595.177  114492.656   
1  129521.270  126804.899  127288.155  128567.089  128818.346  129524.299   
2  143693.317  141102.547  141128.342  143566.703  142998.328  144778.184   
3  157156.675  154942.450  156285.553  157280.127  157213.401  158614.900   
4  171229.330  169463.254  169708.673  173178.120  170930.516  172620.736   

           41          42          43          44          45          46  \
0  113746.198  114952.494  113546.024  113835.934  114055.366  113376.597   
1  129516.042  129709.264  127647.043  127186.665  127433.201  127804.864   
2  142910.169  144120.185  142156.903  143097.466  140534.910  141399.952   
3  157472.237  157981.870  156450.712  156032.079  154540.894  156305.435   
4  170369.183  172610.745  171531.961  171523.145  168211.784  170518.226   

           47          48          49          50          51          52  \
0  114351.332  113481.003  114288.774  113437.268  114112.347  113990.493   
1  129576.575  128882.422  127480.235  127369.033  128041.651  127323.822   
2  144571.666  143369.784  141367.531  141415.035  142611.807  138859.155   
3  159060.085  158171.585  

#### Cautious Portfolio Simulation

In [52]:
# Calculates portfolio expected returns from the portfolio ratios and the predicted returns
# Extracts year and month from the date

stb_b = stb_abs_pred * stb_abs2
stb_g = stb_gtb_pred * stb_GI
axa_b = axa_mmf_pred * axa_mmf2

caut = stb_b.add(stb_g.add(axa_b))
caut.insert(loc = index, column = 'Year', value = dates.to_period('Y'))
caut.insert(loc = index, column = 'Date', value = dates.to_period('M'))
caut.head()

Date  Year         0         1         2         3         4         5  \
0  2019-01  2019  0.011000  0.010202  0.013425  0.009039  0.011654  0.013253   
1  2019-02  2019  0.012448  0.009288  0.013089  0.011101  0.012729  0.014936   
2  2019-03  2019  0.010863  0.012081  0.009241  0.011013  0.010090  0.010639   
3  2019-04  2019  0.014094  0.009312  0.009171  0.014578  0.010634  0.010462   
4  2019-05  2019  0.011858  0.015121  0.010028  0.012422  0.011072  0.014914   

          6         7         8         9        10        11        12  \
0  0.011710  0.015947  0.010527  0.015307  0.011837  0.007898  0.011153   
1  0.010712  0.013103  0.011209  0.008406  0.013119  0.010329  0.010421   
2  0.015735  0.013860  0.010824  0.017217  0.013804  0.014366  0.010326   
3  0.017491  0.011517  0.010846  0.012082  0.010081  0.013363  0.010659   
4  0.010306  0.011941  0.011757  0.012849  0.014604  0.010488  0.011666   

         13        14        15        16        17        18        19  \
0  0.015497  0.008291  0.010593  0.010854  0.014439  0.010880  0.013534   
1  0.014398  0.008141  0.010126  0.015252  0.013948  0.011263  0.008003   
2  0.012188  0.011021  0.011156  0.010081  0.016483  0.011493  0.010538   
3  0.012285  0.012392  0.016434  0.010745  0.012180  0.012992  0.012465   
4  0.012220  0.011074  0.013542  0.014949  0.010185  0.013473  0.012090   

         20        21        22        23        24        25        26  \
0  0.010403  0.011531  0.010510  0.010314  0.012218  0.010295  0.010901   
1  0.014049  0.013478  0.013052  0.012392  0.012626  0.011143  0.011329   
2  0.012223  0.008309  0.013478  0.010335  0.012273  0.009166  0.010848   
3  0.010205  0.010773  0.009355  0.011971  0.012553  0.012822  0.013477   
4  0.010807  0.011149  0.008938  0.014952  0.010993  0.011078  0.013106   

         27        28        29        30        31        32        33  \
0  0.011139  0.014219  0.012317  0.014308  0.013335  0.012461  0.010473   
1  0.011653  0.010726  0.011694  0.014403  0.013895  0.011707  0.011362   
2  0.014666  0.012146  0.012822  0.011323  0.008290  0.012963  0.009135   
3  0.009775  0.010796  0.009817  0.011564  0.009436  0.013237  0.011123   
4  0.015144  0.011830  0.011681  0.010468  0.010860  0.010620  0.013770   

         34        35        36        37        38        39        40  \
0  0.011764  0.009551  0.011970  0.014788  0.014266  0.013293  0.011179   
1  0.014560  0.012770  0.010127  0.014374  0.011095  0.014761  0.007896   
2  0.012396  0.012208  0.009210  0.011739  0.009489  0.015052  0.012259   
3  0.012235  0.012605  0.013084  0.009192  0.014089  0.012298  0.019182   
4  0.012854  0.011763  0.010273  0.010488  0.012550  0.011371  0.011678   

         41        42        43        44        45        46        47  \
0  0.013933  0.006783  0.009551  0.010443  0.012686  0.012312  0.012080   
1  0.010762  0.015017  0.013362  0.007228  0.014118  0.010677  0.013136   
2  0.008460  0.010636  0.014612  0.010895  0.008085  0.013125  0.012539   
3  0.008048  0.011736  0.009287  0.010351  0.011713  0.010866  0.013461   
4  0.009283  0.014748  0.008219  0.014697  0.013877  0.011768  0.009521   

         48        49        50        51        52        53        54  \
0  0.011922  0.012485  0.009485  0.014955  0.009593  0.012896  0.011348   
1  0.011179  0.012514  0.010980  0.014541  0.012675  0.014315  0.012091   
2  0.012008  0.011428  0.014207  0.012924  0.012345  0.010576  0.015318   
3  0.011653  0.013038  0.010539  0.007490  0.012565  0.013764  0.011393   
4  0.013546  0.013752  0.010266  0.012712  0.011984  0.012848  0.009626   

         55        56        57        58        59        60        61  \
0  0.011766  0.010149  0.011941  0.014193  0.012568  0.011298  0.009815   
1  0.012945  0.011957  0.009610  0.015275  0.014217  0.011675  0.009749   
2  0.012278  0.010045  0.012663  0.013276  0.008335  0.011970  0.013671   
3  0.011996  0.010370  0.012258  0.010719  0.009293  0.013042  0.011

In [53]:
# Calculates the nominal monthly returns

caut_ret = pd.concat([caut['Date'], caut['Year'], (caut[list(range(0, 1000))] * 100000)], axis = 1)
caut_df = caut_ret.copy()
caut_nom = caut_df.drop(columns = ['Year'], axis = 1)
caut_nom.head()

Date            0            1            2            3            4  \
0  2019-01  1100.019229  1020.164186  1342.464762   903.944414  1165.393866   
1  2019-02  1244.819527   928.793781  1308.862779  1110.116002  1272.895267   
2  2019-03  1086.288424  1208.099241   924.121114  1101.299354  1009.022755   
3  2019-04  1409.441235   931.195390   917.142057  1457.756446  1063.359218   
4  2019-05  1185.785904  1512.058535  1002.831593  1242.210801  1107.167876   

             5            6            7            8            9  \
0  1325.251417  1171.012113  1594.677798  1052.749481  1530.682434   
1  1493.577811  1071.169862  1310.338589  1120.939687   840.636038   
2  1063.939137  1573.546956  1385.963276  1082.354359  1721.742190   
3  1046.199547  1749.112597  1151.653940  1084.617627  1208.173881   
4  1491.419574  1030.624832  1194.147603  1175.716434  1284.908539   

            10           11           12           13           14  \
0  1183.650771   789.819197  1115.349570  1549.701769   829.097202   
1  1311.926058  1032.908935  1042.065709  1439.847501   814.086862   
2  1380.376914  1436.596700  1032.616927  1218.849288  1102.133186   
3  1008.130142  1336.253686  1065.942718  1228.476556  1239.228934   
4  1460.381912  1048.792484  1166.589813  1222.049925  1107.377544   

            15           16           17           18           19  \
0  1059.325452  1085.422735  1443.939226  1087.951175  1353.448913   
1  1012.606857  1525.240935  1394.792824  1126.273941   800.278993   
2  1115.639541  1008.140539  1648.319938  1149.275501  1053.787786   
3  1643.390120  1074.531111  1217.965374  1299.192583  1246.482029   
4  1354.244389  1494.946944  1018.526612  1347.300703  1209.021743   

            20           21           22           23           24  \
0  1040.264320  1153.148952  1051.047436  1031.385070  1221.824707   
1  1404.853115  1347.833555  1305.204107  1239.153317  1262.623394   
2  1222.298206   830.877917  1347.823498  1033.473891  1227.278300   
3  1020.499195  1077.310604   935.502036  1197.141072  1255.341289   
4  1080.732185  1114.900919   893.804951  1495.207960  1099.269022   

            25           26           27           28           29  \
0  1029.504330  1090.132669  1113.903279  1421.887272  1231.730710   
1  1114.347610  1132.873380  1165.318531  1072.562047  1169.418668   
2   916.627873  1084.803834  1466.566831  1214.634054  1282.153836   
3  1282.234431  1347.702862   977.524766  1079.555332   981.715682   
4  1107.759998  1310.574392  1514.406724  1182.956114  1168.143713   

            30           31           32           33           34  \
0  1430.772133  1333.489099  1246.125930  1047.334959  1176.375968   
1  1440.329334  1389.499899  1170.731721  1136.151155  1455.983561   
2  1132.347798   828.966826  1296.302593   913.495996  1239.589268   
3  1156.438380   943.587962  1323.657053  1112.307170  1223.545662   
4  1046.774703  1086.040297  1062.001120  1377.039274  1285.367951   

            35           36           37           38           39  \
0   955.146036  1196.965843  1478.788123  1426.558742  1329.297978   
1  1276.980163  1012.670484  1437.356809  1109.521499  1476.052861   
2  1220.817441   921.043580  1173.940996   948.913900  1505.244341   
3  1260.525342  1308.406433   919.171539  1408.853527  1229.780473   
4  1176.329507  1027.288697  1048.755904  1255.039693  1137.081369   

            40           41           42           43           44  \
0  1117.907742  1393.334787   678.280468   955.086778  1044.302651   
1   789.634313  1076.188207  1501.670565  1336.156681   722.754764   
2  1225.948492   846.030067  1063.600994  1461.161340  1089.462783   
3  1918.246717   804.800037  1173.621820   928.746006  1035.123794   
4  1167.794648   928.324878  1474.758779   821.857561  1469.712447   

            45           46           47           48           49  \
0  1268.593157  1231.205351  1207.983784  1192.202214  1248.460357   
1  1411.757961  1067.73

In [54]:
# Calculates the cummulative monthly returns

caut_mth = caut_ret.drop(columns = ['Year'], axis = 1)
caut_mth.iloc[:1, 1:] = caut_mth.iloc[:1, 1:] + 100000
caut_mth = round(caut_mth, 3)
caut_mth.iloc[:, 1:] = caut_mth.iloc[:, 1:].cumsum()
caut_mth.head()

Date           0           1           2           3           4  \
0  2019-01  101100.019  101020.164  101342.465  100903.944  101165.394   
1  2019-02  102344.839  101948.958  102651.328  102014.060  102438.289   
2  2019-03  103431.127  103157.057  103575.449  103115.359  103447.312   
3  2019-04  104840.568  104088.252  104492.591  104573.115  104510.671   
4  2019-05  106026.354  105600.311  105495.423  105815.326  105617.839   

            5           6           7           8           9          10  \
0  101325.251  101171.012  101594.678  101052.749  101530.682  101183.651   
1  102818.829  102242.182  102905.017  102173.689  102371.318  102495.577   
2  103882.768  103815.729  104290.980  103256.043  104093.060  103875.954   
3  104928.968  105564.842  105442.634  104340.661  105301.234  104884.084   
4  106420.388  106595.467  106636.782  105516.377  106586.143  106344.466   

           11          12          13          14          15          16  \
0  100789.819  101115.350  101549.702  100829.097  101059.325  101085.423   
1  101822.728  102157.416  102989.550  101643.184  102071.932  102610.664   
2  103259.325  103190.033  104208.399  102745.317  103187.572  103618.805   
3  104595.579  104255.976  105436.876  103984.546  104830.962  104693.336   
4  105644.371  105422.566  106658.926  105091.924  106185.206  106188.283   

           17          18          19          20          21          22  \
0  101443.939  101087.951  101353.449  101040.264  101153.149  101051.047   
1  102838.732  102214.225  102153.728  102445.117  102500.983  102356.251   
2  104487.052  103363.501  103207.516  103667.415  103331.861  103704.074   
3  105705.017  104662.694  104453.998  104687.914  104409.172  104639.576   
4  106723.544  106009.995  105663.020  105768.646  105524.073  105533.381   

           23          24          25          26          27          28  \
0  101031.385  101221.825  101029.504  101090.133  101113.903  101421.887   
1  102270.538  102484.448  102143.852  102223.006  102279.222  102494.449   
2  103304.012  103711.726  103060.480  103307.810  103745.789  103709.083   
3  104501.153  104967.067  104342.714  104655.513  104723.314  104788.638   
4  105996.361  106066.336  105450.474  105966.087  106237.721  105971.594   

           29          30          31          32          33          34  \
0  101231.731  101430.772  101333.489  101246.126  101047.335  101176.376   
1  102401.150  102871.101  102722.989  102416.858  102183.486  102632.360   
2  103683.304  104003.449  103551.956  103713.161  103096.982  103871.949   
3  104665.020  105159.887  104495.544  105036.818  104209.289  105095.495   
4  105833.164  106206.662  105581.584  106098.819  105586.328  106380.863   

           35          36          37          38          39          40  \
0  100955.146  101196.966  101478.788  101426.559  101329.298  101117.908   
1  102232.126  102209.636  102916.145  102536.080  102805.351  101907.542   
2  103452.943  103130.680  104090.086  103484.994  104310.595  103133.490   
3  104713.468  104439.086  105009.258  104893.848  105540.375  105051.737   
4  105889.798  105466.375  106058.014  106148.888  106677.456  106219.532   

           41          42          43          44          45          46  \
0  101393.335  100678.280  100955.087  101044.303  101268.593  101231.205   
1  102469.523  102179.951  102291.244  101767.058  102680.351  102298.942   
2  103315.553  103243.552  103752.405  102856.521  103488.900  103611.471   
3  104120.353  104417.174  104681.151  103891.645  104660.184  104698.030   
4  105048.678  105891.933  105503.009  105361.357  106047.927  105874.861   

           47          48          49          50          51          52  \
0  101207.984  101192.202  101248.460  100948.488  101495.497  100959.281   
1  102521.614  102310.082  102499.857  102046.461  102949.608  102226.782   
2  103775.499  103510.931  103642.658  103467.148  104242.028  103461.292   
3  105121.57

In [55]:
# Calculates the cummulative yearly returns

caut_port = caut_ret.groupby('Year').sum().reset_index()
caut_port.iloc[:1, 1:] = caut_port.iloc[:1, 1:].apply(lambda x: x + 100000)
caut_port = round(caut_port, 3)
caut_port.iloc[:, 1:] = caut_port.iloc[:, 1:].cumsum()
caut_port.head()

Year           0           1           2           3           4  \
0  2019  114347.941  113657.297  113867.015  114095.267  113927.217   
1  2020  128200.168  127782.254  128820.906  127967.474  128490.491   
2  2021  142429.465  141285.262  142579.926  141535.982  142327.758   
3  2022  157365.957  155103.025  155685.514  156254.179  155806.049   
4  2023  171588.199  168748.655  168399.030  171178.084  170757.070   

            5           6           7           8           9          10  \
0  114087.381  113888.646  115412.975  114229.349  116117.526  114299.428   
1  127264.720  128185.720  130082.840  128191.563  130779.565  128216.115   
2  141579.941  143615.663  144063.285  142767.649  146568.650  142642.483   
3  155883.273  157899.762  158286.023  157444.911  160937.343  157892.509   
4  170997.746  171079.011  172413.110  172467.580  175156.860  172407.112   

           11          12          13          14          15          16  \
0  113950.712  114249.004  114957.322  113167.862  113637.462  113990.761   
1  127368.378  128184.294  128502.461  128074.081  127733.131  128027.036   
2  141693.244  143790.848  142616.660  141467.563  141078.654  141660.947   
3  155822.499  156959.206  156565.515  155543.214  156151.552  155994.942   
4  170628.014  170802.119  169933.411  169617.968  168788.011  169628.999   

           17          18          19          20          21          22  \
0  114414.006  114429.537  113416.047  113755.187  114304.886  113952.939   
1  128153.662  129026.207  128619.728  128419.149  127346.685  127741.259   
2  143300.629  143157.454  142505.134  142542.257  142016.781  141756.690   
3  157747.463  156879.711  155606.558  157768.522  156703.934  155934.895   
4  171133.615  170878.944  169380.378  171940.098  171140.562  169856.476   

           23          24          25          26          27          28  \
0  114295.102  114086.893  114169.516  114241.869  115614.425  114854.579   
1  128483.274  128944.037  127964.282  128601.452  129439.300  129409.975   
2  143165.721  142314.785  143171.312  144053.551  143885.852  144062.365   
3  157739.686  155979.989  157090.884  158116.778  158134.726  157904.731   
4  171050.728  169628.826  171738.728  172016.512  173481.711  171626.469   

           29          30          31          32          33          34  \
0  113736.815  115208.479  113699.542  114450.627  113741.997  115482.093   
1  127375.562  129593.607  126589.643  128998.972  127508.187  129588.125   
2  142629.210  143279.660  140152.405  143839.203  141557.467  142731.742   
3  157362.442  156951.307  155346.835  158021.482  156083.943  157175.223   
4  171084.348  171290.990  169656.965  172934.329  170708.797  170519.331   

           35          36          37          38          39          40  \
0  114408.682  113034.678  114558.519  115166.533  114715.815  114703.858   
1  129905.598  127531.142  127525.824  128526.140  128705.694  129560.123   
2  144124.786  141926.575  141525.735  143501.676  143030.145  144612.726   
3  158056.655  155797.714  156798.513  157406.613  157515.883  158917.643   
4  172313.858  170054.199  170530.040  172952.696  171073.727  172813.514   

           41          42          43          44          45          46  \
0  114152.798  114907.611  113728.680  114189.518  114325.231  113666.176   
1  129777.877  129780.680  128074.085  127909.925  128080.326  128185.214   
2  143342.175  144441.337  142443.607  143783.385  141597.479  141973.970   
3  158159.879  158285.398  157152.227  157143.500  155685.478  156715.273   
4  171147.600  173034.353  172271.552  172591.868  169624.222  171050.454   

           47          48          49          50          51          52  \
0  114519.940  113812.569  114599.735  113422.813  114396.146  114341.004   
1  129357.278  128893.418  128026.526  126991.998  128666.004  127898.421   
2  144243.090  143322.413  142266.233  140745.150  143061.297  140258.791   
3  158837.819  158234.180  

#### Balanced Portfolio Simulation

In [56]:
# Calculates portfolio expected returns from the portfolio ratios and the predicted returns
# Extracts year and month from the date

stb_c = stb_abs_pred * stb_abs3
axa_c = axa_mmf_pred * axa_mmf3

bal = stb_c.add(axa_c)
bal.insert(loc = index, column = 'Year', value = dates.to_period('Y'))
bal.insert(loc = index, column = 'Date', value = dates.to_period('M'))
bal.head()

Date  Year         0         1         2         3         4         5  \
0  2019-01  2019  0.013478  0.005912  0.014330  0.010111  0.012798  0.014280   
1  2019-02  2019  0.014449  0.010028  0.015779  0.010957  0.014668  0.014210   
2  2019-03  2019  0.011020  0.011759  0.009611  0.012286  0.008031  0.011162   
3  2019-04  2019  0.010402  0.012120  0.013965  0.014357  0.013931  0.011139   
4  2019-05  2019  0.015449  0.013732  0.010929  0.011352  0.013148  0.014653   

          6         7         8         9        10        11        12  \
0  0.010762  0.009995  0.016030  0.012668  0.012130  0.006057  0.011320   
1  0.009538  0.014697  0.009247  0.010665  0.014050  0.009390  0.010280   
2  0.013748  0.012773  0.014013  0.011755  0.015332  0.015739  0.014473   
3  0.017536  0.012905  0.009480  0.012411  0.015367  0.013623  0.009197   
4  0.010499  0.012979  0.011947  0.014167  0.015092  0.015522  0.014795   

         13        14        15        16        17        18        19  \
0  0.012483  0.012272  0.011995  0.011455  0.015588  0.007898  0.015066   
1  0.017428  0.008854  0.008707  0.015006  0.013147  0.009036  0.012367   
2  0.011644  0.008563  0.010593  0.010534  0.015325  0.012365  0.010815   
3  0.012290  0.010713  0.016518  0.012410  0.011303  0.012378  0.012612   
4  0.008802  0.012442  0.010534  0.010514  0.011565  0.013559  0.013729   

         20        21        22        23        24        25        26  \
0  0.014035  0.010806  0.014129  0.009309  0.010571  0.011026  0.011703   
1  0.014639  0.010810  0.011819  0.014041  0.018847  0.013128  0.012567   
2  0.012098  0.009496  0.010308  0.012194  0.012474  0.007704  0.014743   
3  0.004712  0.013632  0.007363  0.013669  0.013331  0.011467  0.013907   
4  0.010512  0.014065  0.009438  0.012995  0.011569  0.009596  0.012405   

         27        28        29        30        31        32        33  \
0  0.011865  0.016187  0.015009  0.014189  0.013029  0.008509  0.010186   
1  0.013019  0.013355  0.013326  0.015381  0.013499  0.010869  0.012963   
2  0.015936  0.009963  0.014094  0.013948  0.008045  0.014532  0.010674   
3  0.016287  0.013261  0.009456  0.010382  0.012403  0.010974  0.012124   
4  0.015791  0.010637  0.011079  0.011452  0.008936  0.012121  0.014611   

         34        35        36        37        38        39        40  \
0  0.014841  0.010429  0.010812  0.010437  0.014673  0.010996  0.013157   
1  0.014955  0.013333  0.010513  0.014131  0.010670  0.013739  0.011874   
2  0.013618  0.013914  0.009084  0.010682  0.006137  0.017584  0.012742   
3  0.010968  0.012294  0.016175  0.012189  0.013929  0.013142  0.014693   
4  0.010983  0.013137  0.013198  0.009612  0.012103  0.014045  0.014807   

         41        42        43        44        45        46        47  \
0  0.015818  0.006878  0.013376  0.014651  0.013509  0.010199  0.008349   
1  0.010287  0.013482  0.013878  0.009192  0.013126  0.015928  0.012980   
2  0.010556  0.010645  0.009723  0.007939  0.011979  0.013326  0.016066   
3  0.014812  0.009686  0.008741  0.011273  0.009819  0.014284  0.011717   
4  0.014197  0.012813  0.009435  0.017658  0.019633  0.013893  0.011778   

         48        49        50        51        52        53        54  \
0  0.013763  0.009909  0.008576  0.012917  0.012798  0.012115  0.014740   
1  0.013319  0.015415  0.012069  0.019880  0.012998  0.012332  0.014902   
2  0.013748  0.012280  0.015722  0.009449  0.009926  0.012271  0.013966   
3  0.012053  0.011192  0.012725  0.009982  0.014409  0.014673  0.010770   
4  0.012850  0.014479  0.010422  0.009570  0.013569  0.014256  0.013418   

         55        56        57        58        59        60        61  \
0  0.011511  0.010978  0.009287  0.014760  0.012844  0.013357  0.012993   
1  0.012771  0.012036  0.009104  0.015756  0.010688  0.010300  0.011820   
2  0.012711  0.011475  0.012229  0.014426  0.008656  0.012718  0.011456   
3  0.012302  0.010683  0.012754  0.012281  0.009505  0.010015  0.018

In [57]:
# Calculates the nominal monthly returns

bal_ret = pd.concat([bal['Date'], bal['Year'], (bal[list(range(0, 1000))] * 100000)], axis = 1)
bal_df = bal_ret.copy()
bal_nom = bal_df.drop(columns = ['Year'], axis = 1)
bal_nom.head()

Date            0            1            2            3            4  \
0  2019-01  1347.786619   591.248307  1432.973974  1011.118226  1279.794076   
1  2019-02  1444.879183  1002.813123  1577.917413  1095.726270  1466.774027   
2  2019-03  1101.984393  1175.892879   961.117780  1228.637199   803.081797   
3  2019-04  1040.178786  1211.959260  1396.520526  1435.664169  1393.052501   
4  2019-05  1544.915876  1373.234740  1092.861981  1135.154391  1314.835439   

             5            6            7            8            9  \
0  1428.032941  1076.223745   999.499768  1602.964713  1266.814151   
1  1420.963949   953.841813  1469.708345   924.652562  1066.491251   
2  1116.166545  1374.837652  1277.309330  1401.321137  1175.479460   
3  1113.891973  1753.649363  1290.509513   948.001625  1241.134623   
4  1465.302432  1049.895932  1297.943570  1194.665595  1416.733854   

            10           11           12           13           14  \
0  1212.977533   605.739743  1131.984585  1248.295294  1227.160773   
1  1404.961415   938.962557  1027.987296  1742.790159   885.352530   
2  1533.198553  1573.867008  1447.251404  1164.379477   856.276388   
3  1536.724440  1362.346817   919.713553  1229.048555  1071.251531   
4  1509.151570  1552.217858  1479.471238   880.228473  1244.169015   

            15           16           17           18           19  \
0  1199.546926  1145.519675  1558.769463   789.848813  1506.630107   
1   870.677859  1500.589148  1314.719541   903.649527  1236.732480   
2  1059.281876  1053.419477  1532.511390  1236.485148  1081.542580   
3  1651.780507  1240.979558  1130.333930  1237.765089  1261.213209   
4  1053.392401  1051.445192  1156.505453  1355.893338  1372.855271   

            20           21           22           23           24  \
0  1403.450620  1080.637859  1412.869743   930.876119  1057.081567   
1  1463.861269  1080.994787  1181.853824  1404.052574  1884.709902   
2  1209.809236   949.603225  1030.776354  1219.394752  1247.358315   
3   471.174189  1363.248947   736.281243  1366.904426  1333.050833   
4  1051.229505  1406.549094   943.839902  1299.545527  1156.941338   

            25           26           27           28           29  \
0  1102.610639  1170.333418  1186.458621  1618.693491  1500.923636   
1  1312.752550  1256.690898  1301.948507  1335.543960  1332.611860   
2   770.352828  1474.259733  1593.619686   996.311604  1409.395065   
3  1146.726422  1390.726968  1628.700549  1326.128683   945.597734   
4   959.623769  1240.462105  1579.072553  1063.688016  1107.879575   

            30           31           32           33           34  \
0  1418.946730  1302.949039   850.884530  1018.637048  1484.147752   
1  1538.118375  1349.894429  1086.892256  1296.341934  1495.515818   
2  1394.769308   804.510955  1453.168596  1067.370339  1361.788373   
3  1038.227554  1240.337874  1097.371920  1212.413453  1096.821039   
4  1145.206538   893.629030  1212.055095  1461.132438  1098.306249   

            35           36           37           38           39  \
0  1042.935497  1081.199722  1043.666110  1467.310051  1099.550568   
1  1333.335772  1051.277121  1413.130508  1066.990733  1373.868026   
2  1391.375117   908.437934  1068.212611   613.693872  1758.408241   
3  1229.365540  1617.513438  1218.906400  1392.908667  1314.184503   
4  1313.699473  1319.799750   961.181072  1210.278773  1404.495604   

            40           41           42           43           44  \
0  1315.656703  1581.845363   687.766286  1337.616233  1465.065018   
1  1187.394630  1028.720013  1348.223828  1387.788892   919.188761   
2  1274.198155  1055.564074  1064.468821   972.282248   793.926950   
3  1469.331721  1481.241367   968.637975   874.050165  1127.292651   
4  1480.724229  1419.699521  1281.271679   943.546198  1765.832509   

            45           46           47           48           49  \
0  1350.926823  1019.880056   834.876961  1376.268452   990.890161   
1  1312.639619  1592.77

In [58]:
# Calculates the real monthly returns

bal_mth = bal_ret.drop(columns = ['Year'], axis = 1)
bal_mth.iloc[:1, 1:] = bal_mth.iloc[:1, 1:] + 100000
bal_mth = round(bal_mth, 3)
bal_mth.iloc[:, 1:] = bal_mth.iloc[:, 1:].cumsum()
bal_mth.head()

Date           0           1           2           3           4  \
0  2019-01  101347.787  100591.248  101432.974  101011.118  101279.794   
1  2019-02  102792.666  101594.061  103010.891  102106.844  102746.568   
2  2019-03  103894.650  102769.954  103972.009  103335.481  103549.650   
3  2019-04  104934.829  103981.913  105368.530  104771.145  104942.703   
4  2019-05  106479.745  105355.148  106461.392  105906.299  106257.538   

            5           6           7           8           9          10  \
0  101428.033  101076.224  100999.500  101602.965  101266.814  101212.978   
1  102848.997  102030.066  102469.208  102527.618  102333.305  102617.939   
2  103965.164  103404.904  103746.517  103928.939  103508.784  104151.138   
3  105079.056  105158.553  105037.027  104876.941  104749.919  105687.862   
4  106544.358  106208.449  106334.971  106071.607  106166.653  107197.014   

           11          12          13          14          15          16  \
0  100605.740  101131.985  101248.295  101227.161  101199.547  101145.520   
1  101544.703  102159.972  102991.085  102112.514  102070.225  102646.109   
2  103118.570  103607.223  104155.464  102968.790  103129.507  103699.528   
3  104480.917  104526.937  105384.513  104040.042  104781.288  104940.508   
4  106033.135  106006.408  106264.741  105284.211  105834.680  105991.953   

           17          18          19          20          21          22  \
0  101558.769  100789.849  101506.630  101403.451  101080.638  101412.870   
1  102873.489  101693.499  102743.362  102867.312  102161.633  102594.724   
2  104406.000  102929.984  103824.905  104077.121  103111.236  103625.500   
3  105536.334  104167.749  105086.118  104548.295  104474.485  104361.781   
4  106692.839  105523.642  106458.973  105599.525  105881.034  105305.621   

           23          24          25          26          27          28  \
0  100930.876  101057.082  101102.611  101170.333  101186.459  101618.693   
1  102334.929  102941.792  102415.364  102427.024  102488.408  102954.237   
2  103554.324  104189.150  103185.717  103901.284  104082.028  103950.549   
3  104921.228  105522.201  104332.443  105292.011  105710.729  105276.678   
4  106220.774  106679.142  105292.067  106532.473  107289.802  106340.366   

           29          30          31          32          33          34  \
0  101500.924  101418.947  101302.949  100850.885  101018.637  101484.148   
1  102833.536  102957.065  102652.843  101937.777  102314.979  102979.664   
2  104242.931  104351.834  103457.354  103390.946  103382.349  104341.452   
3  105188.529  105390.062  104697.692  104488.318  104594.762  105438.273   
4  106296.409  106535.269  105591.321  105700.373  106055.894  106536.579   

           35          36          37          38          39          40  \
0  101042.935  101081.200  101043.666  101467.310  101099.551  101315.657   
1  102376.271  102132.477  102456.797  102534.301  102473.419  102503.052   
2  103767.646  103040.915  103525.010  103147.995  104231.827  103777.250   
3  104997.012  104658.428  104743.916  104540.904  105546.012  105246.582   
4  106310.711  105978.228  105705.097  105751.183  106950.508  106727.306   

           41          42          43          44          45          46  \
0  101581.845  100687.766  101337.616  101465.065  101350.927  101019.880   
1  102610.565  102035.990  102725.405  102384.254  102663.567  102612.656   
2  103666.129  103100.459  103697.687  103178.181  103861.454  103945.269   
3  105147.370  104069.097  104571.737  104305.474  104843.375  105373.647   
4  106567.070  105350.369  105515.283  106071.307  106806.645  106762.902   

           47          48          49          50          51          52  \
0  100834.877  101376.268  100990.890  100857.566  101291.680  101279.751   
1  102132.870  102708.151  102532.374  102064.445  103279.720  102579.570   
2  103739.448  104082.960  103760.332  103636.661  104224.648  103572.120   
3  104911.11

In [59]:
# Calculates the real yearly returns

bal_port = bal_ret.groupby('Year').sum().reset_index()
bal_port.iloc[:1, 1:] = bal_port.iloc[:1, 1:].apply(lambda x: x + 100000)
bal_port = round(bal_port, 3)
bal_port.iloc[:, 1:] = bal_port.iloc[:, 1:].cumsum()
bal_port.head()

Year           0           1           2           3           4  \
0  2019  115125.570  113988.701  114638.021  113700.000  113335.482   
1  2020  130151.970  129430.841  129427.970  129002.262  128370.432   
2  2021  145514.509  143976.354  143237.127  142909.674  141795.907   
3  2022  161059.845  157260.231  157450.749  157806.772  156771.012   
4  2023  176777.019  171561.445  172722.973  174143.365  172376.448   

            5           6           7           8           9          10  \
0  115014.593  114252.530  114394.216  114683.491  115673.733  116075.373   
1  130610.216  128789.680  129553.946  128950.692  131875.584  131184.909   
2  145210.049  144416.809  144420.467  143495.355  147732.858  146565.325   
3  160905.655  159742.139  160555.665  158130.468  162782.333  161935.093   
4  175665.371  175161.988  175546.566  173922.465  179199.199  177498.849   

           11          12          13          14          15          16  \
0  114685.591  114353.765  115814.521  114402.082  113213.010  115502.504   
1  129768.117  128949.866  130178.582  130646.559  128037.887  129941.329   
2  144889.642  145149.877  144195.775  144352.695  142807.181  145465.460   
3  159756.098  158533.566  158118.891  159696.046  158449.676  160495.124   
4  175560.526  173896.187  172323.910  174946.136  173062.694  175472.779   

           17          18          19          20          21          22  \
0  115257.431  114965.912  115374.905  113947.089  115051.120  113926.065   
1  130609.842  131211.828  131135.211  129774.623  130420.973  128276.937   
2  145841.938  146166.807  146256.359  144743.008  145669.741  143673.501   
3  162467.809  160505.802  160359.100  160539.916  160456.722  158862.474   
4  176592.355  174967.717  175097.814  175260.457  176653.389  173028.653   

           23          24          25          26          27          28  \
0  114896.661  114918.753  114872.351  115801.008  116315.738  114775.794   
1  129699.267  131687.695  128766.407  131845.669  130376.257  130220.021   
2  146087.872  145859.066  144974.572  146965.820  145236.206  146725.531   
3  160192.638  159967.622  158253.507  163377.096  160898.073  162859.286   
4  174676.789  174917.112  174077.796  177859.916  176859.841  177705.076   

           29          30          31          32          33          34  \
0  113768.429  115884.837  114814.679  115188.442  115278.479  114721.134   
1  127485.653  131504.340  129365.551  129381.375  129740.983  129749.935   
2  143181.011  145523.261  145549.957  144269.490  143618.970  145638.868   
3  157843.436  159161.837  161059.222  158323.650  159213.854  160688.544   
4  172034.500  173832.121  176525.101  174784.362  173952.524  175445.823   

           35          36          37          38          39          40  \
0  115495.101  114330.013  115288.789  114537.039  115026.177  116205.106   
1  131647.429  129842.452  128642.575  129090.742  128887.175  130814.546   
2  146401.431  145292.806  142876.408  143994.098  143476.803  145090.884   
3  161530.393  159753.182  159406.238  158843.892  159037.357  161278.101   
4  176252.576  173242.369  174646.326  173607.988  172908.832  174640.958   

           41          42          43          44          45          46  \
0  116035.293  114374.210  113870.166  115693.317  115778.960  115363.079   
1  131443.670  129314.033  129361.073  131112.886  131095.141  129529.182   
2  145690.366  144751.957  143424.591  146834.892  145946.752  144514.829   
3  161166.186  158904.043  159670.530  162070.116  160270.353  159279.771   
4  173847.020  174953.270  175379.060  176600.870  174476.176  173974.403   

           47          48          49          50          51          52  \
0  115174.605  114653.038  115050.770  113493.091  115451.095  115513.624   
1  130082.346  128860.833  130921.227  126445.074  131017.732  130293.938   
2  144462.117  142959.375  147100.126  139731.847  144756.752  145623.748   
3  160644.568  157887.904  

#### Growth Portfolio Simulation

In [60]:
# Calculates portfolio expected returns from the portfolio ratios and the predicted returns
# Extracts year and month from the date

stb_d1 = stb_abs_pred * stb_abs4
stb_d2 = stb_etf_pred * stb_etf1

# 100000 is the invested amount
grow = stb_d1.add(stb_d2)
grow.insert(loc = index, column = 'Year', value = dates.to_period('Y'))
grow.insert(loc = index, column = 'Date', value = dates.to_period('M'))
grow.head()

Date  Year         0         1         2         3         4         5  \
0  2019-01  2019  0.002000  0.015201 -0.006456  0.001610  0.031634 -0.024825   
1  2019-02  2019  0.044568  0.013406  0.014845  0.050868 -0.022559  0.011758   
2  2019-03  2019 -0.028720  0.006097  0.041575  0.008673 -0.004847  0.022877   
3  2019-04  2019 -0.023114  0.039109  0.004929  0.034745 -0.016899  0.037673   
4  2019-05  2019  0.024869 -0.007183 -0.004740 -0.007236  0.018286  0.004974   

          6         7         8         9        10        11        12  \
0  0.008881  0.018114  0.007827  0.041718 -0.009225  0.025007  0.003146   
1 -0.020553  0.010895  0.010106 -0.003573  0.019688 -0.005999  0.000071   
2  0.017657  0.016137 -0.009684  0.010281  0.015243 -0.006490  0.050708   
3  0.030878  0.048753 -0.002184 -0.008636  0.009056  0.026899  0.029425   
4  0.000176 -0.012270  0.018476  0.009949  0.029449 -0.014355  0.002316   

         13        14        15        16        17        18        19  \
0  0.042474  0.037335  0.008247  0.001830  0.008320  0.027691  0.006212   
1  0.002188  0.006288  0.011000  0.014138  0.012628  0.004328  0.046047   
2  0.022217  0.006401  0.008366 -0.000818 -0.002808  0.017735  0.009121   
3 -0.040054  0.000705 -0.014383  0.003682  0.003323 -0.029630 -0.010756   
4  0.004942  0.035577 -0.012362  0.025426  0.007310  0.028039  0.039420   

         20        21        22        23        24        25        26  \
0 -0.000517  0.033030  0.011419  0.022535  0.000586  0.011898  0.010450   
1  0.054475  0.006462  0.014952  0.035603  0.010731 -0.016668  0.001104   
2 -0.002061 -0.017127  0.023595  0.008403  0.026532 -0.000533 -0.003649   
3 -0.019398  0.008824 -0.000884  0.012880  0.038023  0.029258  0.040033   
4 -0.007483  0.019995 -0.021527  0.027451  0.000447  0.024167 -0.001288   

         27        28        29        30        31        32        33  \
0 -0.000178  0.043082  0.016054  0.019701  0.028410  0.015224  0.030040   
1  0.009046  0.009783 -0.001013  0.001813 -0.002037 -0.001883 -0.005333   
2  0.029875  0.041379 -0.016700 -0.035783  0.009726  0.046809  0.006643   
3  0.022060 -0.001542  0.018918 -0.018086 -0.003156  0.002223  0.026755   
4  0.018934  0.020490  0.012292  0.018259 -0.014091  0.021429 -0.004567   

         34        35        36        37        38        39        40  \
0  0.004418  0.020971  0.015072  0.025849 -0.016884  0.036976  0.004855   
1  0.003274  0.040725  0.028326  0.027381  0.007506  0.004736  0.021693   
2  0.002684  0.060443  0.017208 -0.007736  0.013103 -0.001059 -0.037666   
3  0.030955  0.000141 -0.014814 -0.014510 -0.002576  0.006936 -0.000219   
4  0.039991  0.030958  0.010750  0.011990  0.011439 -0.008507  0.027196   

         41        42        43        44        45        46        47  \
0  0.005642  0.003199  0.000507  0.005417  0.018226 -0.001543  0.007257   
1  0.019058 -0.002305  0.010009 -0.016791  0.029268  0.007520 -0.011977   
2  0.023551  0.014285  0.001029  0.030515  0.002657  0.014359 -0.006199   
3  0.040268  0.003118 -0.001303 -0.027652  0.003749  0.025751 -0.020056   
4  0.015141  0.022024  0.019458 -0.000206  0.000514  0.006846  0.002747   

         48        49        50        51        52        53        54  \
0  0.044349  0.004249  0.013729 -0.020730 -0.016106 -0.005530  0.028617   
1  0.004885  0.012811  0.000825 -0.008101  0.015812 -0.013435 -0.019756   
2  0.018737  0.029403  0.015028  0.012595 -0.023529 -0.009982  0.006088   
3 -0.010236  0.026150  0.006826  0.029420  0.025091 -0.000290 -0.010292   
4  0.030598 -0.007113 -0.023347 -0.024283  0.037912  0.014770  0.028776   

         55        56        57        58        59        60        61  \
0 -0.008659 -0.002100  0.041456 -0.013026  0.002909 -0.004627 -0.009757   
1 -0.016312 -0.015446  0.000506  0.046796  0.059399  0.002718  0.027791   
2  0.003224  0.013705  0.029140 -0.027465  0.005995  0.002880  0.045590   
3  0.004777 -0.002832 -0.022692 -0.002712  0.006429 -0.002823 -0.000

In [61]:
# Calculates the nominal monthly returns

grow_ret = pd.concat([grow['Date'], grow['Year'], (grow[list(range(0, 1000))] * 100000)], axis = 1)
grow_df = grow_ret.copy()
grow_nom = grow_df.drop(columns = ['Year'], axis = 1)
grow_nom.head()

Date            0            1            2            3            4  \
0  2019-01   199.954154  1520.079130  -645.550542   160.952110  3163.419532   
1  2019-02  4456.838905  1340.583010  1484.493643  5086.779520 -2255.933972   
2  2019-03 -2871.982140   609.663206  4157.518709   867.321165  -484.651180   
3  2019-04 -2311.356064  3910.864513   492.932988  3474.460936 -1689.855738   
4  2019-05  2486.878103  -718.294907  -473.950881  -723.581627  1828.639082   

             5            6            7            8            9  \
0 -2482.507947   888.084178  1811.350877   782.737327  4171.763658   
1  1175.797120 -2055.266623  1089.521372  1010.574824  -357.274233   
2  2287.654982  1765.666826  1613.664621  -968.363978  1028.092773   
3  3767.269452  3087.797113  4875.333972  -218.418427  -863.568513   
4   497.426086    17.581061 -1226.998562  1847.647936   994.925766   

            10           11           12           13           14  \
0  -922.494130  2500.706428   314.556462  4247.402242  3733.539766   
1  1968.846814  -599.945014     7.140648   218.837286   628.788494   
2  1524.331902  -649.007207  5070.849380  2221.704694   640.078178   
3   905.571941  2689.863611  2942.534715 -4005.396036    70.463142   
4  2944.868232 -1435.522804   231.585748   494.247075  3557.713140   

            15           16           17           18           19  \
0   824.693338   182.988096   831.980755  2769.077233   621.174429   
1  1099.985417  1413.841302  1262.834760   432.804523  4604.719637   
2   836.574429   -81.815533  -280.845797  1773.514650   912.053686   
3 -1438.277826   368.173265   332.294167 -2962.953810 -1075.633700   
4 -1236.220324  2542.628534   730.992466  2803.866287  3942.041189   

            20           21           22           23           24  \
0   -51.749576  3302.952698  1141.898552  2253.490628    58.609411   
1  5447.496152   646.191184  1495.202385  3560.282470  1073.056099   
2  -206.085986 -1712.717207  2359.510970   840.269045  2653.173806   
3 -1939.840505   882.413475   -88.412479  1287.991560  3802.341600   
4  -748.328265  1999.453672 -2152.697278  2745.107839    44.684316   

            25           26           27           28           29  \
0  1189.834640  1044.962062   -17.847786  4308.194997  1605.440103   
1 -1666.806369   110.385679   904.608843   978.308368  -101.284561   
2   -53.348097  -364.936103  2987.528053  4137.850772 -1669.977140   
3  2925.785348  4003.348778  2205.983555  -154.198261  1891.772946   
4  2416.698508  -128.838782  1893.448763  2048.979298  1229.206335   

            30           31           32           33           34  \
0  1970.084928  2840.968008  1522.371986  3004.024648   441.777332   
1   181.329469  -203.738645  -188.295618  -533.277832   327.361340   
2 -3578.282561   972.551492  4680.898466   664.320498   268.396925   
3 -1808.578406  -315.564950   222.261891  2675.522178  3095.467800   
4  1825.895188 -1409.089838  2142.885396  -456.723287  3999.105765   

            35           36           37           38           39  \
0  2097.130627  1507.164350  2584.883144 -1688.446441  3697.594461   
1  4072.530982  2832.597805  2738.058592   750.551742   473.613584   
2  6044.339585  1720.800792  -773.555945  1310.339189  -105.895318   
3    14.093936 -1481.432126 -1450.951314  -257.597929   693.602822   
4  3095.797975  1075.039179  1199.005981  1143.931472  -850.675772   

            40           41           42           43           44  \
0   485.505380   564.192279   319.866753    50.733299   541.671487   
1  2169.250023  1905.782939  -230.450874  1000.945665 -1679.115883   
2 -3766.609758  2355.120073  1428.487775   102.869280  3051.540578   
3   -21.882977  4026.810747   311.783057  -130.291644 -2765.232216   
4  2719.595344  1514.062116  2202.448520  1945.827966   -20.627698   

            45           46           47           48           49  \
0  1822.565775  -154.260770   725.674921  4434.859622   424.916449   
1  2926.753598   751.98

In [62]:
# Calculates the real monthly returns

grow_mth = grow_ret.drop(columns = ['Year'], axis = 1)
grow_mth.iloc[:1, 1:] = grow_mth.iloc[:1, 1:] + 100000
grow_mth = round(grow_mth, 3)
grow_mth.iloc[:, 1:] = grow_mth.iloc[:, 1:].cumsum()
grow_mth.head()

Date           0           1           2           3           4  \
0  2019-01  100199.954  101520.079   99354.449  100160.952  103163.420   
1  2019-02  104656.793  102860.662  100838.943  105247.732  100907.486   
2  2019-03  101784.811  103470.325  104996.462  106115.053  100422.835   
3  2019-04   99473.455  107381.190  105489.395  109589.514   98732.979   
4  2019-05  101960.333  106662.895  105015.444  108865.932  100561.618   

            5           6           7           8           9          10  \
0   97517.492  100888.084  101811.351  100782.737  104171.764   99077.506   
1   98693.289   98832.817  102900.872  101793.312  103814.490  101046.353   
2  100980.944  100598.484  104514.537  100824.948  104842.583  102570.685   
3  104748.213  103686.281  109389.871  100606.530  103979.014  103476.257   
4  105245.639  103703.862  108162.872  102454.178  104973.940  106421.125   

           11          12          13          14          15          16  \
0  102500.706  100314.556  104247.402  103733.540  100824.693  100182.988   
1  101900.761  100321.697  104466.239  104362.328  101924.678  101596.829   
2  101251.754  105392.546  106687.944  105002.406  102761.252  101515.013   
3  103941.618  108335.081  102682.548  105072.869  101322.974  101883.186   
4  102506.095  108566.667  103176.795  108630.582  100086.754  104425.815   

           17          18          19          20          21          22  \
0  100831.981  102769.077  100621.174   99948.250  103302.953  101141.899   
1  102094.816  103201.882  105225.894  105395.746  103949.144  102637.101   
2  101813.970  104975.397  106137.948  105189.660  102236.427  104996.612   
3  102146.264  102012.443  105062.314  103249.819  103118.840  104908.200   
4  102877.256  104816.309  109004.355  102501.491  105118.294  102755.503   

           23          24          25          26          27          28  \
0  102253.491  100058.609  101189.835  101044.962   99982.152  104308.195   
1  105813.773  101131.665   99523.029  101155.348  100886.761  105286.503   
2  106654.042  103784.839   99469.681  100790.412  103874.289  109424.354   
3  107942.034  107587.181  102395.466  104793.761  106080.273  109270.156   
4  110687.142  107631.865  104812.165  104664.922  107973.722  111319.135   

           29          30          31          32          33          34  \
0  101605.440  101970.085  102840.968  101522.372  103004.025  100441.777   
1  101504.155  102151.414  102637.229  101334.076  102470.747  100769.138   
2   99834.178   98573.131  103609.780  106014.974  103135.067  101037.535   
3  101725.951   96764.553  103294.215  106237.236  105810.589  104133.003   
4  102955.157   98590.448  101885.125  108380.121  105353.866  108132.109   

           35          36          37          38          39          40  \
0  102097.131  101507.164  102584.883   98311.554  103697.594  100485.505   
1  106169.662  104339.762  105322.942   99062.106  104171.208  102654.755   
2  112214.002  106060.563  104549.386  100372.445  104065.313   98888.145   
3  112228.096  104579.131  103098.435  100114.847  104758.916   98866.262   
4  115323.894  105654.170  104297.441  101258.778  103908.240  101585.857   

           41          42          43          44          45          46  \
0  100564.192  100319.867  100050.733  100541.671  101822.566   99845.739   
1  102469.975  100089.416  101051.679   98862.555  104749.320  100597.726   
2  104825.095  101517.904  101154.548  101914.096  105015.020  102033.597   
3  108851.906  101829.687  101024.256   99148.864  105389.955  104608.694   
4  110365.968  104032.136  102970.084   99128.236  105441.361  105293.247   

           47          48          49          50          51          52  \
0  100725.675  104434.860  100424.916  101372.870   97927.032   98389.445   
1   99527.940  104923.386  101706.034  101455.398   97116.948   99970.681   
2   98908.090  106797.052  104646.323  102958.165   98376.446   97617.795   
3   96902.48

In [63]:
# Calculates the real yearlt returns

grow_port = grow_ret.groupby('Year').sum().reset_index()
grow_port.iloc[:1, 1:] = grow_port.iloc[:1, 1:].apply(lambda x: x + 100000)
grow_port = round(grow_port, 3)
grow_port.iloc[:, 1:] = grow_port.iloc[:, 1:].cumsum()
grow_port.head()

Year           0           1           2           3           4  \
0  2019  115280.055  123538.921  112893.513  115992.423  109774.707   
1  2020  129929.090  134004.798  125890.290  129373.813  126632.631   
2  2021  142938.481  148846.069  134627.302  143151.149  127384.800   
3  2022  153256.182  157354.804  140793.982  156150.909  142370.282   
4  2023  162505.488  170529.478  154195.192  166606.397  157019.405   

            5           6           7           8           9          10  \
0  112060.587  106652.805  122570.518  116057.922  112384.041  125117.676   
1  117325.146  129170.273  132516.967  140615.831  120882.526  136109.442   
2  131844.188  136401.796  159846.169  150579.477  132049.509  154510.848   
3  146139.273  147138.512  176347.935  155038.057  142823.956  180899.813   
4  167046.554  150323.779  191704.320  147900.221  160654.185  194442.969   

           11          12          13          14          15          16  \
0  105781.290  109845.339  111230.035  116968.780  104121.808  112105.559   
1  116529.827  130533.407  130927.031  124053.035  113752.481  127619.182   
2  123833.668  149023.362  143882.228  136906.304  137853.952  147020.268   
3  134703.317  159505.393  158746.616  144368.111  151815.047  160834.125   
4  149017.901  167200.364  167987.761  134380.687  165677.933  171448.881   

           17          18          19          20          21          22  \
0  109812.420  120500.322  110408.683  109550.158  107722.147  104955.013   
1  125324.949  139301.082  128786.645  118254.466  115980.184  113289.113   
2  130544.013  143641.709  138869.206  125029.602  123873.054  138899.320   
3  149513.078  156825.025  151306.607  123697.613  131666.732  158127.820   
4  164754.724  174474.897  164665.803  129760.733  143247.680  172545.285   

           23          24          25          26          27          28  \
0  123775.793  116625.809  110504.825  106983.200  123836.951  119945.729   
1  145921.485  148543.498  123943.910  124443.773  134148.456  135843.190   
2  165884.126  170076.833  135795.168  129991.379  140980.822  154547.086   
3  189960.596  186486.505  150992.174  131361.728  153542.835  173952.443   
4  200237.723  190603.108  163049.378  151987.215  161445.481  199969.679   

           29          30          31          32          33          34  \
0  100995.782  109311.681  110342.536  115782.736  111374.877  114388.335   
1  112099.728  123237.881  124707.968  116731.362  122481.897  129150.653   
2  118296.955  134603.650  141698.426  133731.815  131942.623  138434.109   
3  133559.512  150219.498  167041.613  149618.793  148404.533  139520.123   
4  144892.113  166223.904  175402.502  153308.748  165898.288  152204.848   

           35          36          37          38          39          40  \
0  118720.202  105003.726  102746.991  114046.293  118652.999  116910.902   
1  129883.031  112239.764  123307.397  135917.303  135294.644  131488.676   
2  148589.561  121764.644  143374.947  139707.167  141059.001  150236.689   
3  141670.355  124006.657  149472.007  149875.365  148167.794  163838.005   
4  152184.962  140082.790  159190.172  165875.873  161536.817  173496.423   

           41          42          43          44          45          46  \
0  115664.666  116159.796  108785.881  106908.815  107005.440  118033.713   
1  128594.432  112259.756  136432.181  115832.444  111920.824  135402.735   
2  145732.759  117986.212  140773.784  112411.448  122847.564  144382.962   
3  155204.834  127697.844  157779.321  122114.959  126334.565  153075.380   
4  164869.385  135774.875  179556.049  133051.270  138962.903  165025.101   

           47          48          49          50          51          52  \
0  106446.172  111675.891  110870.974  105989.170  103246.541  108488.163   
1  116758.816  114881.942  130665.235  115410.725  132060.548  113394.444   
2  127407.107  117419.099  143964.937  120170.484  137944.843  128131.405   
3  136854.516  125616.867  

#### Aggressive Portfolio Simulation

In [64]:
# Calculates portfolio expected returns from the portfolio ratios and the predicted returns
# Extracts year and month from the date

stb_e1 = stb_abs_pred * stb_abs5
stb_e2 = stb_etf_pred * stb_etf2

aggres = stb_e1.add(stb_e2)
aggres.insert(loc = index, column = 'Year', value = dates.to_period('Y'))
aggres.insert(loc = index, column = 'Date', value = dates.to_period('M'))
aggres.head()

Date  Year         0         1         2         3         4         5  \
0  2019-01  2019 -0.007766  0.023538 -0.023579 -0.005571  0.046759 -0.056853   
1  2019-02  2019  0.068760  0.016056  0.013665  0.083434 -0.053132  0.009911   
2  2019-03  2019 -0.061018  0.001626  0.067513  0.005640 -0.015023  0.032286   
3  2019-04  2019 -0.049842  0.060642 -0.003183  0.051441 -0.042612  0.059219   
4  2019-05  2019  0.031934 -0.023921 -0.017701 -0.022137  0.022176 -0.002905   

          6         7         8         9        10        11        12  \
0  0.007503  0.025630  0.000213  0.065895 -0.026653  0.040683 -0.003511   
1 -0.044935  0.007552  0.011094 -0.015555  0.024130 -0.018361 -0.008194   
2  0.021251  0.019125 -0.029497  0.010010  0.014880 -0.024823  0.079530   
3  0.041748  0.077728 -0.011484 -0.025758  0.003022  0.037730  0.046149   
4 -0.008228 -0.033058  0.023722  0.006250  0.041064 -0.039500 -0.008433   

         13        14        15        16        17        18        19  \
0  0.067486  0.057057  0.004850 -0.006037  0.002148  0.044283 -0.001205   
1 -0.010719  0.004047  0.013070  0.013483  0.012258  0.000885  0.072752   
2  0.030932  0.005019  0.006667 -0.010108 -0.017378  0.021983  0.007799   
3 -0.082736 -0.007154 -0.039496 -0.003709 -0.002971 -0.063762 -0.029790   
4  0.002391  0.054149 -0.030503  0.038350  0.003587  0.039815  0.060104   

         20        21        22        23        24        25        26  \
0 -0.013011  0.051235  0.008564  0.033419 -0.007230  0.012493  0.009239   
1  0.086894  0.003341  0.017703  0.052834  0.003048 -0.041237 -0.008419   
2 -0.013598 -0.039102  0.034957  0.004997  0.037934 -0.007059 -0.019352   
3 -0.038061  0.004392 -0.007234  0.011989  0.057980  0.043920  0.061243   
4 -0.022172  0.024329 -0.046876  0.039636 -0.008688  0.036309 -0.012354   

         27        28        29        30        31        32        33  \
0 -0.010083  0.064639  0.016470  0.024199  0.040956  0.021413  0.046228   
1  0.005563  0.006370 -0.012961 -0.009322 -0.014616 -0.012151 -0.020495   
2  0.041028  0.067377 -0.041952 -0.076784  0.011149  0.072782  0.003028   
3  0.025649 -0.014004  0.026686 -0.041078 -0.016322 -0.004438  0.038492   
4  0.021435  0.028703  0.013415  0.023632 -0.032462  0.028828 -0.020326   

         34        35        36        37        38        39        40  \
0 -0.004599  0.029457  0.018746  0.039170 -0.042649  0.058523 -0.002283   
1 -0.006272  0.062997  0.042738  0.038209  0.005002 -0.002452  0.029085   
2 -0.006483  0.098044  0.023865 -0.022615  0.019421 -0.016644 -0.078808   
3  0.047512 -0.009739 -0.040593 -0.036744 -0.015988  0.001688 -0.011595   
4  0.063972  0.045304  0.008261  0.014081  0.010989 -0.027278  0.036817   

         41        42        43        44        45        46        47  \
0 -0.002983  0.000142 -0.010752 -0.002776  0.021912 -0.010784  0.006993   
1  0.026283 -0.014858  0.006801 -0.038288  0.042687 -0.000199 -0.032301   
2  0.033794  0.017194 -0.005281  0.049363 -0.005619  0.015154 -0.024977   
3  0.059889 -0.001929 -0.009412 -0.059486 -0.000874  0.034556 -0.045616   
4  0.015133  0.029904  0.027413 -0.015242 -0.016035  0.000691 -0.005018   

         48        49        50        51        52        53        54  \
0  0.068884  0.000063  0.018078 -0.047852 -0.040206 -0.019787  0.039282   
1 -0.002350  0.010153 -0.008564 -0.031790  0.018045 -0.034049 -0.048453   
2  0.022423  0.043223  0.014264  0.015705 -0.050333 -0.028454 -0.000025   
3 -0.028483  0.038625  0.001644  0.044851  0.033439 -0.012660 -0.027323   
4  0.045231 -0.024802 -0.050891 -0.051337  0.057527  0.014927  0.040682   

         55        56        57        58        59        60        61  \
0 -0.025023 -0.012872  0.068068 -0.035670 -0.005254 -0.019673 -0.028855   
1 -0.040000 -0.037795 -0.006490  0.072067  0.099676 -0.003262  0.040426   
2 -0.004592  0.015259  0.043024 -0.061780  0.003771 -0.005199  0.073842   
3 -0.001392 -0.013857 -0.051647 -0.015201  0.003932 -0.012757 -0.016

In [65]:
# Calculates the nominal monthly returns

aggres_ret = pd.concat([aggres['Date'], aggres['Year'], (aggres[list(range(0, 1000))] * 100000)], axis = 1)
aggres_df = aggres_ret.copy()
aggres_nom = aggres_df.drop(columns = ['Year'], axis = 1)
aggres_nom.head()

Date            0            1            2            3            4  \
0  2019-01  -776.609593  2353.756487 -2357.873445  -557.088570  4675.909074   
1  2019-02  6876.020544  1605.590307  1366.539156  8343.448941 -5313.162617   
2  2019-03 -6101.767430   162.591169  6751.267691   563.976364 -1502.253909   
3  2019-04 -4984.155239  6064.165851  -318.292355  5144.078911 -4261.193494   
4  2019-05  3193.380623 -2392.149484 -1770.053187 -2213.677184  2217.624240   

             5            6            7            8            9  \
0 -5685.338932   750.257054  2562.975697    21.322182  6589.546038   
1   991.116508 -4493.454363   755.176662  1109.359479 -1555.471395   
2  3228.618832  2125.118109  1912.539541 -2949.727471  1001.001554   
3  5921.894850  4174.809561  7772.841329 -1148.449720 -2575.808376   
4  -290.507668  -822.814252 -3305.842818  2372.189326   625.030641   

            10           11           12           13           14  \
0 -2665.326997  4068.262194  -351.149969  6748.602879  5705.684671   
1  2412.951701 -1836.139376  -819.423933 -1071.868806   404.704029   
2  1488.044335 -2482.255506  7952.999043  3093.238840   501.937743   
3   302.159634  3773.038586  4614.911100 -8273.604484  -715.446277   
4  4106.357492 -3950.045341  -843.278742   239.090773  5414.902319   

            15           16           17           18           19  \
0   485.025747  -603.676544   214.843315  4428.301776  -120.487323   
1  1306.965527  1348.325148  1225.789651    88.507857  7275.212243   
2   666.681546 -1010.838483 -1737.841603  2198.302230   779.942680   
3 -3949.624199  -370.900194  -297.141363 -6376.187874 -2978.976031   
4 -3050.331614  3835.009340   358.680489  3981.453649  6010.364896   

            20           21           22           23           24  \
0 -1301.139214  5123.515517   856.384685  3341.911360  -722.976588   
1  8689.398533   334.093204  1770.265741  5283.449796   304.802960   
2 -1359.799766 -3910.235083  3495.719668   499.689437  3793.446152   
3 -3806.148406   439.178292  -723.433130  1198.899721  5798.021460   
4 -2217.176672  2432.857730 -4687.619003  3963.618524  -868.788632   

            25           26           27           28           29  \
0  1249.349827   923.905342 -1008.307058  6463.859401  1646.978800   
1 -4123.732978  -841.887523   556.319932   636.997610 -1296.132342   
2  -705.924448 -1935.195619  4102.770883  6737.668465 -4195.193581   
3  4392.036937  6124.344902  2564.853619 -1400.427245  2668.593780   
4  3630.901367 -1235.353779  2143.534706  2870.313806  1341.470895   

            30           31           32           33           34  \
0  2419.920852  4095.630291  2141.323732  4622.825618  -459.878928   
1  -932.219038 -1461.571093 -1215.089378 -2049.477511  -627.243895   
2 -7678.444013  1114.860739  7278.216838   302.811319  -648.333186   
3 -4107.799332 -1632.192169  -443.800628  3849.209146  4751.180633   
4  2363.176912 -3246.228381  2882.848685 -2032.552463  6397.171974   

            35           36           37           38           39  \
0  2945.726613  1874.618622  3916.981616 -4264.888516  5852.311489   
1  6299.661956  4273.755500  3820.877567   500.199210  -245.209496   
2  9804.408432  2386.539247 -2261.537498  1942.095948 -1664.363092   
3  -973.864031 -4059.326009 -3674.382504 -1598.831428   168.826112   
4  4530.422821   826.073849  1408.091205  1098.869361 -2727.752317   

            40           41           42           43           44  \
0  -228.328153  -298.310597    14.194203 -1075.190789  -277.570981   
1  2908.549019  2628.303361 -1485.842468   680.107449 -3828.778104   
2 -7880.843760  3379.403982  1719.449736  -528.119921  4936.327530   
3 -1159.543382  5988.857721  -192.885086  -941.213256 -5948.567594   
4  3681.749456  1513.349235  2990.369300  2741.315679 -1524.233002   

            45           46           47           48           49  \
0  2191.220394 -1078.385770   699.290853  6888.400444     6.332077   
1  4268.664966   -19.91

In [66]:
# Calculates the real monthly returns

aggres_mth = aggres_ret.drop(columns = ['Year'], axis = 1)
aggres_mth.iloc[:1, 1:] = aggres_mth.iloc[:1, 1:] + 100000
aggres_mth = round(aggres_mth, 3)
aggres_mth.iloc[:, 1:] = aggres_mth.iloc[:, 1:].cumsum()
aggres_mth.head()

Date           0           1           2           3           4  \
0  2019-01   99223.390  102353.756   97642.127   99442.911  104675.909   
1  2019-02  106099.411  103959.346   99008.666  107786.360   99362.746   
2  2019-03   99997.644  104121.937  105759.934  108350.336   97860.492   
3  2019-04   95013.489  110186.103  105441.642  113494.415   93599.299   
4  2019-05   98206.870  107793.954  103671.589  111280.738   95816.923   

            5           6           7           8           9          10  \
0   94314.661  100750.257  102562.976  100021.322  106589.546   97334.673   
1   95305.778   96256.803  103318.153  101130.681  105034.075   99747.625   
2   98534.397   98381.921  105230.693   98180.954  106035.077  101235.669   
3  104456.292  102556.731  113003.534   97032.504  103459.269  101537.829   
4  104165.784  101733.917  109697.691   99404.693  104084.300  105644.186   

           11          12          13          14          15          16  \
0  104068.262   99648.850  106748.603  105705.685  100485.026   99396.323   
1  102232.123   98829.426  105676.734  106110.389  101791.992  100744.648   
2   99749.867  106782.425  108769.973  106612.327  102458.674   99733.810   
3  103522.906  111397.336  100496.369  105896.881   98509.050   99362.910   
4   99572.861  110554.057  100735.460  111311.783   95458.718  103197.919   

           17          18          19          20          21          22  \
0  100214.843  104428.302   99879.513   98698.861  105123.516  100856.385   
1  101440.633  104516.810  107154.725  107388.260  105457.609  102626.651   
2   99702.791  106715.112  107934.668  106028.460  101547.374  106122.371   
3   99405.650  100338.924  104955.692  102222.312  101986.552  105398.938   
4   99764.330  104320.378  110966.057  100005.135  104419.410  100711.319   

           23          24          25          26          27          28  \
0  103341.911   99277.023  101249.350  100923.905   98991.693  106463.859   
1  108625.361   99581.826   97125.617  100082.017   99548.013  107100.857   
2  109125.050  103375.272   96419.693   98146.821  103650.784  113838.525   
3  110323.950  109173.293  100811.730  104271.166  106215.638  112438.098   
4  114287.569  108304.504  104442.631  103035.812  108359.173  115308.412   

           29          30          31          32          33          34  \
0  101646.979  102419.921  104095.630  102141.324  104622.826   99540.121   
1  100350.847  101487.702  102634.059  100926.235  102573.348   98912.877   
2   96155.653   93809.258  103748.920  108204.452  102876.159   98264.544   
3   98824.247   89701.459  102116.728  107760.651  106725.368  103015.725   
4  100165.718   92064.636   98870.500  110643.500  104692.816  109412.897   

           35          36          37         38          39          40  \
0  102945.727  101874.619  103916.982  95735.111  105852.311   99771.672   
1  109245.389  106148.375  107737.860  96235.310  105607.102  102680.221   
2  119049.797  108534.914  105476.323  98177.406  103942.739   94799.377   
3  118075.933  104475.588  101801.940  96578.575  104111.565   93639.834   
4  122606.356  105301.662  103210.031  97677.444  101383.813   97321.583   

           41          42          43          44          45          46  \
0   99701.689  100014.194   98924.809   99722.429  102191.220   98921.614   
1  102329.992   98528.352   99604.916   95893.651  106459.885   98901.702   
2  105709.396  100247.802   99076.796  100829.979  105898.021  100417.062   
3  111698.254  100054.917   98135.583   94881.411  105810.641  103872.633   
4  113211.603  103045.286  100876.899   93357.178  104207.178  103941.686   

           47          48          49          50         51          52  \
0  100699.291  106888.400  100006.332  101807.849  95214.789   95979.386   
1   97469.167  106653.388  101021.609  100951.434  92035.762   97783.868   
2   94971.499  108895.669  105343.883  102377.801  93606.254   92750.556   
3   90409.853  106047.

In [67]:
# Calculates the real yearly retyurns

aggres_port = aggres_ret.groupby('Year').sum().reset_index()
aggres_port.iloc[:1, 1:] = aggres_port.iloc[:1, 1:].apply(lambda x: x + 100000)
aggres_port = round(aggres_port, 3)
aggres_port.iloc[:, 1:] = aggres_port.iloc[:, 1:].cumsum()
aggres_port.head()

Year           0           1           2           3           4  \
0  2019  115276.542  131275.224  111340.050  117972.663  106998.575   
1  2020  129416.221  137440.680  122913.184  129544.178  125255.724   
2  2021  140305.209  152346.658  127530.539  143128.725  115771.223   
3  2022  146267.158  157071.246  126939.666  154524.000  130525.583   
4  2023  149984.737  169223.823  138360.743  159976.066  144267.675   

            5           6           7           8           9          10  \
0  109495.297  100381.003  129410.653  117088.207  109808.456  132176.348   
1  105940.778  129386.736  135040.615  150001.201  111780.675  139612.860   
2  120356.675  129739.182  172345.206  156255.776  119118.880  160308.059   
3  133272.535  136552.742  188804.481  152425.595  126307.016  195649.821   
4  159233.561  129405.765  204312.622  126488.704  144917.123  207363.342   

           11          12          13          14          15          16  \
0   98403.815  106145.902  107357.720  118844.107   96795.941  109086.460   
1  105330.800  131666.167  131292.626  118241.492  102073.953  125416.638   
2  106127.614  151921.129  143394.712  130338.768  133550.546  147631.823   
3  113634.367  159996.368  159063.052  131175.765  146041.284  160318.582   
4  126563.418  161201.750  164121.153  100445.891  158943.339  167136.214   

           17          18          19          20          21          22  \
0  105215.181  124904.104  106044.190  105942.888  101626.274   97635.414   
1  120583.008  145520.804  126494.218  108635.174  103712.113  100954.591   
2  117654.329  141054.559  132250.593  108573.820  105496.837  134651.208   
3  138155.527  153183.195  143139.015   93185.437  107590.271  156967.050   
4  154159.746  173356.018  155223.461   92102.758  115104.505  171559.020   

           23          24          25          26          27          28  \
0  130915.058  117869.035  106822.856   99532.372  129863.301  124183.201   
1  158920.312  161819.028  119844.755  117848.698  137094.208  140310.704   
2  181487.704  189208.013  128000.601  115669.228  137319.309  160470.147   
3  213765.291  207416.771  144876.406  104412.858  147118.996  182148.772   
4  220430.226  202493.108  153691.567  129945.456  148347.054  217082.301   

           29          30          31          32          33          34  \
0   90588.145  103841.399  106519.857  116147.242  107927.474  114281.195   
1   99545.479  116175.529  120442.290  106382.166  116181.185  128701.116   
2   97916.415  125308.074  137663.855  125116.075  122067.481  132140.105   
3  113694.705  142542.289  170995.742  142531.815  139048.995  121765.432   
4  122612.483  159580.796  173367.544  135538.998  158786.982  132532.777   

           35          36          37          38          39          40  \
0  121164.530   97163.231   92416.980  113782.188  121548.896  117250.421   
1  128152.886   97478.967  118773.892  141407.648  140506.076  131860.474   
2  149999.937  102017.111  143540.688  136155.317  139023.118  154386.551   
3  124886.426   94218.066  140948.147  142352.555  139060.199  165557.488   
4  131883.286  112543.997  145917.014  159516.496  151998.582  172285.926   

           41          42          43          44          45          46  \
0  115047.772  117694.269  104598.539   99495.561   99619.538  119936.512   
1  126007.654   98418.047  141958.031  102841.601   95793.548  139951.384   
2  145384.841   96090.175  138439.475   83848.575  103281.519  143847.011   
3  149839.275  102143.710  155795.396   88728.277   97895.005  147610.780   
4  157075.844  103529.485  182430.288   96867.889  109164.396  157257.621   

           47          48          49          50          51          52  \
0   99220.861  109088.836  107360.389   99867.184   93117.924  102554.181   
1  105833.030  103494.706  129983.284  106546.878  132500.843   99215.898   
2  113525.503   96664.965  140621.727  104463.143  132099.327  112947.805   
3  117252.059   99360.975  

#### Dollar Portfolio Simulation

In [68]:
# Calculates portfolio expected returns from the portfolio ratios and the predicted returns
# Extracts year and month from the date

stb_f = stb_euro_pred * stb_euro
fbn_a = fbn_euro_pred * fbn_euro

doll = stb_f.add(fbn_a)
doll.insert(loc = index, column = 'Year', value = dates.to_period('Y'))
doll.insert(loc = index, column = 'Date', value = dates.to_period('M'))
doll.head()

Date  Year         0         1         2         3         4         5  \
0  2019-01  2019  0.010668  0.008791  0.002597  0.009967  0.003820  0.000125   
1  2019-02  2019  0.000189 -0.002135  0.001945  0.000325  0.004601  0.001481   
2  2019-03  2019  0.003525  0.001250  0.000784 -0.012985 -0.002596 -0.000980   
3  2019-04  2019  0.009476 -0.007451  0.001994  0.004756 -0.003364  0.002499   
4  2019-05  2019  0.003573  0.002212  0.003949  0.012933  0.005447  0.004290   

          6         7         8         9        10        11        12  \
0  0.002756 -0.000472 -0.001155 -0.006287  0.005703  0.012018 -0.005672   
1  0.003840  0.008054  0.013837  0.003794  0.002943  0.006429 -0.000621   
2  0.007413  0.010020  0.009850  0.002868  0.002007 -0.006436 -0.008630   
3  0.014026  0.004680  0.004876  0.001888 -0.001686 -0.007595  0.006924   
4 -0.004402  0.014396  0.004715  0.006609  0.006733  0.006961  0.010859   

         13        14        15        16        17        18        19  \
0  0.006527 -0.000604 -0.003087  0.003473 -0.001519  0.003783 -0.001258   
1  0.007233 -0.001955  0.004251  0.000603  0.006254 -0.005341 -0.005725   
2  0.010028 -0.001937  0.010252  0.003903 -0.003666  0.002279 -0.002920   
3  0.006201 -0.000030 -0.007482  0.009980  0.006016  0.001014  0.003191   
4 -0.000787 -0.002159  0.004057  0.010153 -0.002858 -0.006117  0.004999   

         20        21        22        23        24        25        26  \
0  0.000240  0.006835 -0.000934 -0.001111 -0.001426  0.000762  0.000492   
1  0.003362 -0.006759  0.006353  0.008029 -0.004725 -0.001803 -0.011105   
2 -0.001851 -0.011645  0.002526  0.010743  0.009033  0.005466 -0.002936   
3 -0.008432  0.008814  0.008381 -0.003649  0.001162 -0.004034  0.005569   
4  0.003818  0.004357  0.000750  0.003001  0.007261 -0.000987  0.007603   

         27        28        29        30        31        32        33  \
0  0.005171  0.013661  0.008208  0.007486  0.005403 -0.003636  0.004311   
1  0.005531 -0.006350  0.003215  0.000012  0.001236 -0.004054  0.002559   
2  0.014247  0.000915  0.002405  0.011798  0.002689 -0.016275  0.009923   
3 -0.007984  0.008820  0.006219 -0.004884  0.003898  0.001581  0.003803   
4 -0.001546  0.000573  0.004615  0.007054  0.004320  0.002898  0.012779   

         34        35        36        37        38        39        40  \
0 -0.001959  0.000359  0.008349 -0.008786  0.002249 -0.011700  0.008038   
1  0.002290  0.002923 -0.000113 -0.001076 -0.008785  0.012187  0.003747   
2  0.007808  0.006163  0.013744  0.003934 -0.000542 -0.001035  0.004694   
3  0.003590 -0.000097 -0.006438 -0.003998 -0.005691  0.010067 -0.006435   
4 -0.004250  0.000735  0.010630  0.007925  0.009440  0.002650 -0.003181   

         41        42        43        44        45        46        47  \
0  0.005550  0.001097  0.005548 -0.001048 -0.015396  0.010130  0.001015   
1  0.002328 -0.005872  0.011226  0.008579 -0.003282  0.006863  0.004621   
2  0.002345  0.015723  0.000802  0.010459  0.002953 -0.003674 -0.000038   
3  0.009790  0.010789  0.010437  0.016424  0.014578  0.015303 -0.001563   
4  0.012433  0.002032 -0.005713  0.001644  0.009315 -0.000509  0.001544   

         48        49        50        51        52        53        54  \
0  0.013992  0.001635 -0.003277 -0.000484 -0.007246  0.007974  0.000237   
1 -0.000965  0.002878  0.008670  0.005011  0.005861  0.003310 -0.004828   
2 -0.000936  0.012957  0.006288  0.009206  0.002739  0.003546  0.000379   
3  0.001851  0.001744 -0.004988 -0.003370 -0.010591  0.018853 -0.000010   
4  0.003943  0.007982  0.006491  0.001630  0.009902  0.000062  0.008181   

         55        56        57        58        59        60        61  \
0  0.006769 -0.002840  0.001151  0.008494  0.006724 -0.005500 -0.005190   
1  0.002488  0.009256  0.004652  0.009598 -0.001478 -0.006115  0.001928   
2  0.005753 -0.001295 -0.000439  0.008796  0.001603  0.012411  0.000930   
3 -0.009233  0.002195 -0.002569 -0.006712 -0.004801  0.010745 -0.005

In [69]:
# Calculates the nominal monthly returns

doll_ret = pd.concat([doll['Date'], doll['Year'], (doll[list(range(0, 1000))] * 100000)], axis = 1)
doll_df = doll_ret.copy()
doll_nom = doll_df.drop(columns = ['Year'], axis = 1)
doll_nom.head()

Date            0           1           2            3           4  \
0  2019-01  1066.786141  879.079690  259.692731   996.707650  381.993434   
1  2019-02    18.858541 -213.491324  194.538993    32.543981  460.133201   
2  2019-03   352.475954  124.953563   78.407449 -1298.450382 -259.587638   
3  2019-04   947.557893 -745.110450  199.424649   475.584609 -336.444763   
4  2019-05   357.281233  221.202716  394.910954  1293.259452  544.650553   

            5            6            7            8           9          10  \
0   12.469646   275.629965   -47.190330  -115.542752 -628.684113  570.287511   
1  148.053698   383.973300   805.435179  1383.711549  379.429784  294.250124   
2  -97.985687   741.304595  1001.956034   984.995115  286.785513  200.675339   
3  249.860761  1402.647481   468.036159   487.560905  188.784302 -168.554693   
4  429.009030  -440.160321  1439.648778   471.516017  660.892365  673.348673   

            11           12           13          14           15  \
0  1201.769050  -567.173043   652.663057  -60.398268  -308.719623   
1   642.864737   -62.075032   723.327420 -195.515208   425.137103   
2  -643.642680  -863.031717  1002.832607 -193.670448  1025.231339   
3  -759.540195   692.423064   620.117076   -2.973350  -748.151361   
4   696.116051  1085.930235   -78.748660 -215.863290   405.650952   

            16          17          18          19          20           21  \
0   347.258640 -151.855961  378.309894 -125.817028   24.036332   683.523829   
1    60.287681  625.416604 -534.063676 -572.484852  336.178775  -675.944060   
2   390.326236 -366.618214  227.889042 -291.979626 -185.087677 -1164.485929   
3   997.978407  601.586418  101.371525  319.130060 -843.193399   881.447182   
4  1015.292674 -285.808381 -611.697377  499.887820  381.818561   435.702338   

           22           23          24          25           26           27  \
0  -93.397238  -111.076571 -142.605315   76.190720    49.162723   517.076564   
1  635.254166   802.877774 -472.534125 -180.280226 -1110.494685   553.125341   
2  252.620651  1074.335517  903.272848  546.648145  -293.583390  1424.736356   
3  838.054622  -364.938570  116.160220 -403.366364   556.909933  -798.359802   
4   75.010585   300.110671  726.114472  -98.668790   760.270815  -154.563050   

            28          29           30          31           32           33  \
0  1366.064644  820.841897   748.553593  540.331706  -363.631138   431.109457   
1  -634.988704  321.460293     1.177474  123.626812  -405.382130   255.861885   
2    91.505853  240.520613  1179.757525  268.896937 -1627.535891   992.265726   
3   881.975754  621.914541  -488.387147  389.770293   158.066264   380.271876   
4    57.333359  461.501513   705.394923  432.026472   289.780629  1277.868837   

           34          35           36          37          38           39  \
0 -195.929133   35.948257   834.933031 -878.634691  224.894709 -1170.021514   
1  229.019943  292.255900   -11.328031 -107.597952 -878.494552  1218.677698   
2  780.758122  616.333526  1374.362423  393.394174  -54.204839  -103.467020   
3  359.015558   -9.735627  -643.795513 -399.798355 -569.061621  1006.725832   
4 -424.968058   73.532827  1063.027277  792.503093  943.957638   264.972302   

           40           41           42           43           44  \
0  803.766729   554.970895   109.688416   554.834001  -104.773064   
1  374.693810   232.826662  -587.209286  1122.610684   857.947094   
2  469.379710   234.453601  1572.274879    80.243407  1045.889714   
3 -643.510829   978.980412  1078.938611  1043.665599  1642.384132   
4 -318.050368  1243.328452   203.197301  -571.339376   164.392441   

            45           46          47           48           49          50  \
0 -1539.639546  1013.021069  101.519082  1399.199992   163.486887 -327.686336   
1  -328.154837   686.336750  462.136436   -96.472815   287.755004  867.047655   
2   295.321799  -367.353837   -3.842155   -93.592748  1295.741917  628.756526

In [70]:
# Calculates the real monthly returns

doll_mth = doll_ret.drop(columns = ['Year'], axis = 1)
doll_mth.iloc[:1, 1:] = doll_mth.iloc[:1, 1:] + 100000
doll_mth = round(doll_mth, 3)
doll_mth.iloc[:, 1:] = doll_mth.iloc[:, 1:].cumsum()
doll_mth.head()

Date           0           1           2           3           4  \
0  2019-01  101066.786  100879.080  100259.693  100996.708  100381.993   
1  2019-02  101085.645  100665.589  100454.232  101029.252  100842.126   
2  2019-03  101438.121  100790.543  100532.639   99730.802  100582.538   
3  2019-04  102385.679  100045.433  100732.064  100206.387  100246.093   
4  2019-05  102742.960  100266.636  101126.975  101499.646  100790.744   

            5           6           7           8           9          10  \
0  100012.470  100275.630   99952.810   99884.457   99371.316  100570.288   
1  100160.524  100659.603  100758.245  101268.169   99750.746  100864.538   
2  100062.538  101400.908  101760.201  102253.164  100037.532  101065.213   
3  100312.399  102803.555  102228.237  102740.725  100226.316  100896.658   
4  100741.408  102363.395  103667.886  103212.241  100887.208  101570.007   

           11          12          13         14          15          16  \
0  101201.769   99432.827  100652.663  99939.602   99691.280  100347.259   
1  101844.634   99370.752  101375.990  99744.087  100116.417  100407.547   
2  101200.991   98507.720  102378.823  99550.417  101141.648  100797.873   
3  100441.451   99200.143  102998.940  99547.444  100393.497  101795.851   
4  101137.567  100286.073  102920.191  99331.581  100799.148  102811.144   

           17          18         19          20          21          22  \
0   99848.144  100378.310  99874.183  100024.036  100683.524   99906.603   
1  100473.561   99844.246  99301.698  100360.215  100007.580  100541.857   
2  100106.943  100072.135  99009.718  100175.127   98843.094  100794.478   
3  100708.529  100173.507  99328.848   99331.934   99724.541  101632.533   
4  100422.721   99561.810  99828.736   99713.753  100160.243  101707.544   

           23          24          25          26          27          28  \
0   99888.923   99857.395  100076.191  100049.163  100517.077  101366.065   
1  100691.801   99384.861   99895.911   98938.668  101070.202  100731.076   
2  101766.137  100288.134  100442.559   98645.085  102494.938  100822.582   
3  101401.198  100404.294  100039.193   99201.995  101696.578  101704.558   
4  101701.309  101130.408   99940.524   99962.266  101542.015  101761.891   

           29          30          31         32          33          34  \
0  100820.842  100748.554  100540.332  99636.369  100431.109   99804.071   
1  101142.302  100749.731  100663.959  99230.987  100686.971  100033.091   
2  101382.823  101929.489  100932.856  97603.451  101679.237  100813.849   
3  102004.738  101441.102  101322.626  97761.517  102059.509  101172.865   
4  102466.240  102146.497  101754.652  98051.298  103337.378  100747.897   

           35          36         37          38          39          40  \
0  100035.948  100834.933  99121.365  100224.895   98829.978  100803.767   
1  100328.204  100823.605  99013.767   99346.400  100048.656  101178.461   
2  100944.538  102197.967  99407.161   99292.195   99945.189  101647.841   
3  100934.802  101554.171  99007.363   98723.133  100951.915  101004.330   
4  101008.335  102617.198  99799.866   99667.091  101216.887  100686.280   

           41          42          43          44          45          46  \
0  100554.971  100109.688  100554.834   99895.227   98460.360  101013.021   
1  100787.798   99522.479  101677.445  100753.174   98132.205  101699.358   
2  101022.252  101094.754  101757.688  101799.064   98427.527  101332.004   
3  102001.232  102173.693  102801.354  103441.448   99885.366  102862.307   
4  103244.560  102376.890  102230.015  103605.840  100816.837  102811.437   

           47          48          49          50          51          52  \
0  100101.519  101399.200  100163.487   99672.314   99951.639   99275.392   
1  100563.655  101302.727  100451.242  100539.362  100452.742   99861.510   
2  100559.813  101209.134  101746.984  101168.119  101373.340  100135.449   
3  100403.497  101394.193  101921.35

In [71]:
# Calculates the real yearly returns 

doll_port = doll_ret.groupby('Year').sum().reset_index()
doll_port.iloc[:1, 1:] = doll_port.iloc[:1, 1:].apply(lambda x: x + 100000)
doll_port = round(doll_port, 3)
doll_port.iloc[:, 1:] = doll_port.iloc[:, 1:].cumsum()
doll_port.head()

Year           0           1           2           3           4  \
0  2019  106819.859  103846.142  103055.966  104987.233  100723.514   
1  2020  110315.682  104828.103  102628.148  110697.918  102633.867   
2  2021  115069.459  107594.293  105505.990  116142.978  103651.075   
3  2022  117291.599  113399.068  106789.973  118297.775  104290.957   
4  2023  122972.257  116046.862  107039.102  117323.333  109341.198   

            5           6           7           8           9          10  \
0  104686.360  104922.034  104019.372  103922.595  101027.573  106603.830   
1  106159.665  111168.310  109667.674  106683.847  103716.598  107982.813   
2  113292.341  117135.213  112441.922  112374.397  109794.936  112741.139   
3  109298.014  122551.700  116631.470  114865.757  115500.762  112217.867   
4  108702.215  126694.197  122056.206  120927.597  120979.770  118550.909   

           11          12          13          14          15          16  \
0  104858.189  101916.160  104664.315   99474.066  103824.462  103725.379   
1  110524.721  106155.628  104809.585  101494.191  110421.027  105416.712   
2  111361.361  110366.054  105530.101  105669.193  113142.100  111014.110   
3  116866.495  115449.732  107325.353  106827.666  115238.125  114687.277   
4  118755.711  120626.138  115121.154  110769.700  116703.952  118681.051   

           17          18          19          20          21          22  \
0  100949.624  101882.776   98893.499  100931.375   99552.334  104571.976   
1  100663.259  106733.378  100803.632  106511.984  107506.695  108863.935   
2  104131.047  106917.929  103745.420  112045.724  112964.260  112500.561   
3  109281.547  108247.624  106914.690  116715.497  116085.972  117997.777   
4  108918.837  107856.712  106244.301  117900.741  121394.367  120585.105   

           23          24          25          26          27          28  \
0   99554.236  104030.074  101535.626  102997.082  106892.420  103669.144   
1  107038.381  106075.331  106478.779  108187.118  109320.358  109301.762   
2  111865.188  110955.930  112086.882  113126.734  110341.539  113266.111   
3  113920.719  116055.868  112504.339  117846.316  114419.935  116957.959   
4  116244.984  120776.695  117765.257  120997.787  119457.208  119386.714   

           29          30          31          32          33          34  \
0  105059.756  104914.450  104304.996  102673.595  102186.356  103951.899   
1  107363.953  109609.855  106849.449  107973.335  106973.931  104552.337   
2  109076.015  114541.582  111768.459  111672.773  108822.126  111789.457   
3  110303.474  118584.519  113174.958  117282.839  111187.637  110453.128   
4  111776.440  121533.431  116084.989  116670.684  113238.796  114775.134   

           35          36          37          38          39          40  \
0  102884.252  101711.004   99830.393  102337.464  103321.301  102372.846   
1  101741.781  109715.647  101188.281  104776.740  110663.775  112869.222   
2  106432.643  115452.739  103600.573  105300.327  111191.460  120391.414   
3  108975.794  117265.046  107500.379  110010.076  115272.295  119652.107   
4  110734.111  122129.920  113844.875  115377.704  119215.283  121669.301   

           41          42          43          44          45          46  \
0  104386.852  101793.923  105220.546  104525.701  100410.765  105890.507   
1  108476.333  102846.232  109348.656  108491.842  104661.799  111140.347   
2  109940.679  107982.199  110737.363  112165.085  104554.874  116055.904   
3  112232.590  109418.796  111703.593  119651.098  109102.433  119176.044   
4  112664.981  111524.607  115726.429  122211.359  111840.853  119617.570   

           47          48          49          50          51          52  \
0  105138.260  102445.148  104009.998  104513.505  105661.320  101922.718   
1  104118.153  107274.233  105687.813  110611.155  109242.609  106942.522   
2  107145.007  112785.838  104415.569  115713.000  115170.620  105519.102   
3  110980.230  114923.159  

In [72]:
pip freeze requirements.txt

alabaster==0.7.12
altair==4.1.0
anaconda-client==1.7.2
anaconda-navigator==1.9.12
anaconda-project==0.8.3
asn1crypto==1.0.1
astor==0.8.1
astroid==2.3.1
astropy==3.2.1
atomicwrites==1.3.0
attrs==19.2.0
Babel==2.7.0
backcall==0.1.0
backports.functools-lru-cache==1.6.1
backports.os==0.1.1
backports.shutil-get-terminal-size==1.0.0
backports.tempfile==1.0
backports.weakref==1.0.post1
base58==2.0.0
beautifulsoup4==4.8.0
bitarray==1.0.1
bkcharts==0.2
bleach==3.1.0
blinker==1.4
bokeh==1.3.4
boto==2.49.0
boto3==1.12.43
botocore==1.15.43
Bottleneck==1.2.1
cachetools==4.1.0
certifi==2019.9.11
cffi==1.12.3
chardet==3.0.4
Click==7.0
cloudpickle==1.2.2
clyent==1.2.2
colorama==0.4.1
colorcet==2.0.2
comtypes==1.1.7
conda==4.8.3
conda-build==3.18.9
conda-package-handling==1.6.0
conda-verify==3.4.2
contextlib2==0.6.0
cryptography==2.7
cycler==0.10.0
Cython==0.29.13
cytoolz==0.10.0
dask==2.5.2
decorator==4.4.0
defusedxml==0.6.0
distributed==2.5.2
docutils==0.15.2
entrypoints==0.3
enum-compat==0.0.3
et-xm

In [73]:
# pip install -r requirements.txt

In [74]:
@Ignore this cell

###### Conservative Portfolio
conserv.to_csv('/content/drive/My Drive/WealthHat Portfolios/conservative_returns.csv')
conserv_nom.to_csv('/content/drive/My Drive/WealthHat Portfolios/conservative_nominal_returns.csv')
conserv_mth.to_csv('/content/drive/My Drive/WealthHat Portfolios/conservative_monthly_aggregate.csv')
conserv_port.to_csv('/content/drive/My Drive/WealthHat Portfolios/conservative_yearly_aggregate.csv')

###### Cautious Portfolio
caut.to_csv('/content/drive/My Drive/WealthHat Portfolios/cautious_returns.csv')
caut_nom.to_csv('/content/drive/My Drive/WealthHat Portfolios/cautious_nominal_returns.csv')
caut_mth.to_csv('/content/drive/My Drive/WealthHat Portfolios/cautious_monthly_aggregate.csv')
caut_port.to_csv('/content/drive/My Drive/WealthHat Portfolios/cautious_yearly_aggregate.csv')

###### Balanced Portfolio
bal.to_csv('/content/drive/My Drive/WealthHat Portfolios/balanced_returns.csv')
bal_nom.to_csv('/content/drive/My Drive/WealthHat Portfolios/balanced_nominal_returns.csv')
bal_mth.to_csv('/content/drive/My Drive/WealthHat Portfolios/balanced_monthly_aggregate.csv')
bal_port.to_csv('/content/drive/My Drive/WealthHat Portfolios/balanced_yearly_aggregate.csv')

###### Growth Portfolio
grow.to_csv('/content/drive/My Drive/WealthHat Portfolios/growth_returns.csv')
grow_nom.to_csv('/content/drive/My Drive/WealthHat Portfolios/growth_nominal_returns.csv')
grow_mth.to_csv('/content/drive/My Drive/WealthHat Portfolios/growth_monthly_aggregate.csv')
grow_port.to_csv('/content/drive/My Drive/WealthHat Portfolios/growth_yearly_aggregate.csv')

###### Aggressive Portfolio
aggres.to_csv('/content/drive/My Drive/WealthHat Portfolios/aggressive_returns.csv')
aggres_nom.to_csv('/content/drive/My Drive/WealthHat Portfolios/aggressive_nominal_returns.csv')
aggres_mth.to_csv('/content/drive/My Drive/WealthHat Portfolios/aggressive_monthly_aggregate.csv')
aggres_port.to_csv('/content/drive/My Drive/WealthHat Portfolios/aggressive_yearly_aggregate.csv')

###### Dollar Portfolio
doll.to_csv('/content/drive/My Drive/WealthHat Portfolios/dollar_returns.csv')
doll_nom.to_csv('/content/drive/My Drive/WealthHat Portfolios/dollar_nominal_returns.csv')
doll_mth.to_csv('/content/drive/My Drive/WealthHat Portfolios/dollar_monthly_aggregate.csv')
doll_port.to_csv('/content/drive/My Drive/WealthHat Portfolios/dollar_yearly_aggregate.csv')

SyntaxError: invalid syntax (<ipython-input-74-ad4a1c9bb123>, line 1)